# Pandas DataFrame to GeoTiff
---
This notebook is concerned with converting the DataFrame rows into GeoTiff pixels. This requires the results of NB # 7, which are too big to be uploaded to the Github repository.

In [1]:
import numpy as np
import pandas as pd
import rasterio as rio
import math
from datetime import datetime

In [2]:
tif_file_name = "data/PHL_wind-speed_100m.tif"
with rio.open(tif_file_name) as img:
    affine_matrix = img.transform
    inverse_affine = ~affine_matrix
    band_id = 1 # Read the raster's first band to process the image's pixels
    band_arr = img.read(band_id)
    img_width = band_arr.shape[1]
    img_height = band_arr.shape[0]
    img_dtype = band_arr.dtype
img.close()

In [3]:
print(affine_matrix)
print(inverse_affine)
print(img_width, img_height, img_dtype)

| 0.00, 0.00, 116.04|
| 0.00,-0.00, 22.18|
| 0.00, 0.00, 1.00|
| 400.00, 0.00,-46416.63|
| 0.00,-400.00, 8871.31|
| 0.00, 0.00, 1.00|
5561 7671 float32


In [20]:
scaled2020_df = pd.read_pickle("results/scaled2020.pkl")
scaled2020_df

x     y       lat         lon    factor  lstm_tanh  lstm_relu  \
0          134  5232  9.098269  116.376572  1.254462   5.751730   5.265032   
1          134  5233  9.095769  116.376572  1.254097   5.750052   5.263496   
2          134  5234  9.093268  116.376572  1.253762   5.748519   5.262093   
3          134  5235  9.090769  116.376572  1.253468   5.747171   5.260859   
4          134  5236  9.088268  116.376572  1.253229   5.746074   5.259854   
...        ...   ...       ...         ...       ...        ...        ...   
21664646  4633  6311  6.400769  127.624069  1.254530   6.065407   4.895267   
21664647  4633  6312  6.398269  127.624069  1.254552   6.065515   4.895355   
21664648  4633  6313  6.395769  127.624069  1.254573   6.065614   4.895435   
21664649  4633  6314  6.393269  127.624069  1.254603   6.065763   4.895555   
21664650  4633  6315  6.390769  127.624069  1.255187   6.068583   4.897831   

           prophet  
0         5.393835  
1         5.392262  
2         5.390824  
3         5.389560  
4         5.388530  
...            ...  
21664646  5.842289  
21664647  5.842393  
21664648  5.842489  
21664649  5.842632  
21664650  5.845349  

[21664651 rows x 8 columns]

In [5]:
scaled2019_df = pd.read_pickle("results/scaled2019.pkl")
scaled2019_df

x     y       lat         lon    factor  lstm_tanh  lstm_relu  \
0          134  5232  9.098269  116.376573  1.254463   5.947391   5.477990   
1          134  5233  9.095769  116.376573  1.254097   5.945656   5.476392   
2          134  5234  9.093269  116.376573  1.253762   5.944071   5.474931   
3          134  5235  9.090769  116.376573  1.253468   5.942677   5.473647   
4          134  5236  9.088269  116.376573  1.253229   5.941542   5.472602   
...        ...   ...       ...         ...       ...        ...        ...   
21664646  4633  6311  6.400769  127.624073  1.254530   6.808452   5.572455   
21664647  4633  6312  6.398269  127.624073  1.254552   6.808573   5.572555   
21664648  4633  6313  6.395769  127.624073  1.254573   6.808685   5.572646   
21664649  4633  6314  6.393269  127.624073  1.254603   6.808852   5.572783   
21664650  4633  6315  6.390769  127.624073  1.255187   6.812018   5.575374   

           prophet  
0         5.433600  
1         5.432015  
2         5.430566  
3         5.429293  
4         5.428256  
...            ...  
21664646  5.753285  
21664647  5.753387  
21664648  5.753481  
21664649  5.753622  
21664650  5.756298  

[21664651 rows x 8 columns]

In [6]:
scaled2018_df = pd.read_pickle("results/scaled2018.pkl")
scaled2018_df

x     y       lat         lon    factor  lstm_tanh  lstm_relu  \
0          134  5232  9.098269  116.376573  1.254463   6.167920   5.754912   
1          134  5233  9.095769  116.376573  1.254097   6.166121   5.753234   
2          134  5234  9.093269  116.376573  1.253762   6.164477   5.751699   
3          134  5235  9.090769  116.376573  1.253468   6.163031   5.750351   
4          134  5236  9.088269  116.376573  1.253229   6.161854   5.749253   
...        ...   ...       ...         ...       ...        ...        ...   
21664646  4633  6311  6.400769  127.624073  1.254530   6.494652   5.363570   
21664647  4633  6312  6.398269  127.624073  1.254552   6.494768   5.363666   
21664648  4633  6313  6.395769  127.624073  1.254573   6.494874   5.363754   
21664649  4633  6314  6.393269  127.624073  1.254603   6.495033   5.363885   
21664650  4633  6315  6.390769  127.624073  1.255187   6.498054   5.366380   

           prophet  
0         5.511928  
1         5.510321  
2         5.508851  
3         5.507559  
4         5.506508  
...            ...  
21664646  5.775729  
21664647  5.775832  
21664648  5.775926  
21664649  5.776068  
21664650  5.778754  

[21664651 rows x 8 columns]

In [8]:
features = scaled2020_df.columns[5:].tolist()
features

['lstm_tanh', 'lstm_relu', 'prophet']

In [7]:
def create_tif_band(df, feature):
    time_now = datetime.now().strftime("%H:%M:%S")
    print("Start creating tif band at %s..." % (time_now))

    band = np.full([img_height, img_width], np.nan)
    for i in range(len(df)):
        if i % 10000 == 0:
            time_now = datetime.now().strftime("%H:%M:%S")
            print("i: %d at %s..." % (i, time_now))
        row = df.iloc[i:i+1]
        band[row.y, row.x] = row[feature]

    time_now = datetime.now().strftime("%H:%M:%S")
    print("Done creating tif band at %s..." % (time_now))
    return band

In [8]:
def create_tif_map(band, year, feature):
    time_now = datetime.now().strftime("%H:%M:%S")
    print("Start writing to tif image at %s..." % (time_now))

    filename = "results/scaled" + str(year) + "_" + str(feature) + ".tif"
    with rio.open(
        filename,
        "w",
        driver="GTiff",
        width=img_width,
        height=img_height,
        dtype="float64",
        count=1,
        crs="+proj=latlong",
        transform=affine_matrix
    ) as scaled_img:

        scaled_img.write(band, 1)
        scaled_img.close()

    time_now = datetime.now().strftime("%H:%M:%S")
    print("Done writing to tif image at %s..." % (time_now))

In [11]:
scaled2020_th_band = create_tif_band(scaled2020_df, features[0])
print(scaled2020_th_band.shape)

Start creating tif band at 22:14:08...
i: 0 at 22:14:09...
i: 100 at 22:14:09...
i: 200 at 22:14:09...
i: 300 at 22:14:09...
i: 400 at 22:14:09...
i: 500 at 22:14:09...
i: 600 at 22:14:09...
i: 700 at 22:14:09...
i: 800 at 22:14:09...
i: 900 at 22:14:09...
i: 1000 at 22:14:09...
i: 1100 at 22:14:09...
i: 1200 at 22:14:09...
i: 1300 at 22:14:09...
i: 1400 at 22:14:09...
i: 1500 at 22:14:09...
i: 1600 at 22:14:09...
i: 1700 at 22:14:09...
i: 1800 at 22:14:09...
i: 1900 at 22:14:09...
i: 2000 at 22:14:09...
i: 2100 at 22:14:09...
i: 2200 at 22:14:09...
i: 2300 at 22:14:09...
i: 2400 at 22:14:09...
i: 2500 at 22:14:09...
i: 2600 at 22:14:09...
i: 2700 at 22:14:09...
i: 2800 at 22:14:09...
i: 2900 at 22:14:09...
i: 3000 at 22:14:09...
i: 3100 at 22:14:09...
i: 3200 at 22:14:09...
i: 3300 at 22:14:09...
i: 3400 at 22:14:09...
i: 3500 at 22:14:09...
i: 3600 at 22:14:09...
i: 3700 at 22:14:09...
i: 3800 at 22:14:09...
i: 3900 at 22:14:09...
i: 4000 at 22:14:09...
i: 4100 at 22:14:09...
i: 4200

i: 35200 at 22:14:16...
i: 35300 at 22:14:16...
i: 35400 at 22:14:16...
i: 35500 at 22:14:16...
i: 35600 at 22:14:16...
i: 35700 at 22:14:16...
i: 35800 at 22:14:16...
i: 35900 at 22:14:17...
i: 36000 at 22:14:17...
i: 36100 at 22:14:17...
i: 36200 at 22:14:17...
i: 36300 at 22:14:17...
i: 36400 at 22:14:17...
i: 36500 at 22:14:17...
i: 36600 at 22:14:17...
i: 36700 at 22:14:17...
i: 36800 at 22:14:17...
i: 36900 at 22:14:17...
i: 37000 at 22:14:17...
i: 37100 at 22:14:17...
i: 37200 at 22:14:17...
i: 37300 at 22:14:17...
i: 37400 at 22:14:17...
i: 37500 at 22:14:17...
i: 37600 at 22:14:17...
i: 37700 at 22:14:17...
i: 37800 at 22:14:17...
i: 37900 at 22:14:17...
i: 38000 at 22:14:17...
i: 38100 at 22:14:17...
i: 38200 at 22:14:17...
i: 38300 at 22:14:17...
i: 38400 at 22:14:17...
i: 38500 at 22:14:17...
i: 38600 at 22:14:17...
i: 38700 at 22:14:17...
i: 38800 at 22:14:17...
i: 38900 at 22:14:17...
i: 39000 at 22:14:17...
i: 39100 at 22:14:17...
i: 39200 at 22:14:17...
i: 39300 at 22:1

i: 69500 at 22:14:24...
i: 69600 at 22:14:24...
i: 69700 at 22:14:24...
i: 69800 at 22:14:24...
i: 69900 at 22:14:24...
i: 70000 at 22:14:24...
i: 70100 at 22:14:24...
i: 70200 at 22:14:24...
i: 70300 at 22:14:24...
i: 70400 at 22:14:24...
i: 70500 at 22:14:24...
i: 70600 at 22:14:24...
i: 70700 at 22:14:24...
i: 70800 at 22:14:24...
i: 70900 at 22:14:24...
i: 71000 at 22:14:24...
i: 71100 at 22:14:24...
i: 71200 at 22:14:24...
i: 71300 at 22:14:24...
i: 71400 at 22:14:24...
i: 71500 at 22:14:24...
i: 71600 at 22:14:24...
i: 71700 at 22:14:24...
i: 71800 at 22:14:24...
i: 71900 at 22:14:24...
i: 72000 at 22:14:24...
i: 72100 at 22:14:24...
i: 72200 at 22:14:24...
i: 72300 at 22:14:24...
i: 72400 at 22:14:24...
i: 72500 at 22:14:24...
i: 72600 at 22:14:24...
i: 72700 at 22:14:24...
i: 72800 at 22:14:24...
i: 72900 at 22:14:24...
i: 73000 at 22:14:24...
i: 73100 at 22:14:24...
i: 73200 at 22:14:24...
i: 73300 at 22:14:24...
i: 73400 at 22:14:25...
i: 73500 at 22:14:25...
i: 73600 at 22:1

i: 103500 at 22:14:31...
i: 103600 at 22:14:31...
i: 103700 at 22:14:31...
i: 103800 at 22:14:31...
i: 103900 at 22:14:31...
i: 104000 at 22:14:31...
i: 104100 at 22:14:31...
i: 104200 at 22:14:31...
i: 104300 at 22:14:31...
i: 104400 at 22:14:31...
i: 104500 at 22:14:31...
i: 104600 at 22:14:31...
i: 104700 at 22:14:31...
i: 104800 at 22:14:31...
i: 104900 at 22:14:31...
i: 105000 at 22:14:31...
i: 105100 at 22:14:32...
i: 105200 at 22:14:32...
i: 105300 at 22:14:32...
i: 105400 at 22:14:32...
i: 105500 at 22:14:32...
i: 105600 at 22:14:32...
i: 105700 at 22:14:32...
i: 105800 at 22:14:32...
i: 105900 at 22:14:32...
i: 106000 at 22:14:32...
i: 106100 at 22:14:32...
i: 106200 at 22:14:32...
i: 106300 at 22:14:32...
i: 106400 at 22:14:32...
i: 106500 at 22:14:32...
i: 106600 at 22:14:32...
i: 106700 at 22:14:32...
i: 106800 at 22:14:32...
i: 106900 at 22:14:32...
i: 107000 at 22:14:32...
i: 107100 at 22:14:32...
i: 107200 at 22:14:32...
i: 107300 at 22:14:32...
i: 107400 at 22:14:32...


i: 136700 at 22:14:39...
i: 136800 at 22:14:39...
i: 136900 at 22:14:39...
i: 137000 at 22:14:39...
i: 137100 at 22:14:39...
i: 137200 at 22:14:39...
i: 137300 at 22:14:39...
i: 137400 at 22:14:39...
i: 137500 at 22:14:39...
i: 137600 at 22:14:39...
i: 137700 at 22:14:39...
i: 137800 at 22:14:39...
i: 137900 at 22:14:39...
i: 138000 at 22:14:39...
i: 138100 at 22:14:39...
i: 138200 at 22:14:39...
i: 138300 at 22:14:39...
i: 138400 at 22:14:39...
i: 138500 at 22:14:39...
i: 138600 at 22:14:39...
i: 138700 at 22:14:39...
i: 138800 at 22:14:39...
i: 138900 at 22:14:39...
i: 139000 at 22:14:39...
i: 139100 at 22:14:39...
i: 139200 at 22:14:39...
i: 139300 at 22:14:39...
i: 139400 at 22:14:39...
i: 139500 at 22:14:39...
i: 139600 at 22:14:39...
i: 139700 at 22:14:39...
i: 139800 at 22:14:39...
i: 139900 at 22:14:39...
i: 140000 at 22:14:39...
i: 140100 at 22:14:39...
i: 140200 at 22:14:39...
i: 140300 at 22:14:39...
i: 140400 at 22:14:39...
i: 140500 at 22:14:39...
i: 140600 at 22:14:39...


...

i: 21521300 at 23:31:13...
i: 21521400 at 23:31:13...
i: 21521500 at 23:31:13...
i: 21521600 at 23:31:13...
i: 21521700 at 23:31:13...
i: 21521800 at 23:31:13...
i: 21521900 at 23:31:13...
i: 21522000 at 23:31:13...
i: 21522100 at 23:31:13...
i: 21522200 at 23:31:13...
i: 21522300 at 23:31:13...
i: 21522400 at 23:31:13...
i: 21522500 at 23:31:13...
i: 21522600 at 23:31:13...
i: 21522700 at 23:31:13...
i: 21522800 at 23:31:13...
i: 21522900 at 23:31:13...
i: 21523000 at 23:31:13...
i: 21523100 at 23:31:13...
i: 21523200 at 23:31:13...
i: 21523300 at 23:31:13...
i: 21523400 at 23:31:13...
i: 21523500 at 23:31:13...
i: 21523600 at 23:31:13...
i: 21523700 at 23:31:13...
i: 21523800 at 23:31:13...
i: 21523900 at 23:31:13...
i: 21524000 at 23:31:13...
i: 21524100 at 23:31:13...
i: 21524200 at 23:31:13...
i: 21524300 at 23:31:13...
i: 21524400 at 23:31:13...
i: 21524500 at 23:31:13...
i: 21524600 at 23:31:13...
i: 21524700 at 23:31:13...
i: 21524800 at 23:31:13...
i: 21524900 at 23:31:14...
i

i: 21552200 at 23:31:19...
i: 21552300 at 23:31:19...
i: 21552400 at 23:31:19...
i: 21552500 at 23:31:19...
i: 21552600 at 23:31:19...
i: 21552700 at 23:31:19...
i: 21552800 at 23:31:19...
i: 21552900 at 23:31:19...
i: 21553000 at 23:31:19...
i: 21553100 at 23:31:19...
i: 21553200 at 23:31:19...
i: 21553300 at 23:31:19...
i: 21553400 at 23:31:19...
i: 21553500 at 23:31:19...
i: 21553600 at 23:31:19...
i: 21553700 at 23:31:19...
i: 21553800 at 23:31:19...
i: 21553900 at 23:31:19...
i: 21554000 at 23:31:19...
i: 21554100 at 23:31:19...
i: 21554200 at 23:31:19...
i: 21554300 at 23:31:19...
i: 21554400 at 23:31:19...
i: 21554500 at 23:31:19...
i: 21554600 at 23:31:19...
i: 21554700 at 23:31:19...
i: 21554800 at 23:31:19...
i: 21554900 at 23:31:19...
i: 21555000 at 23:31:20...
i: 21555100 at 23:31:20...
i: 21555200 at 23:31:20...
i: 21555300 at 23:31:20...
i: 21555400 at 23:31:20...
i: 21555500 at 23:31:20...
i: 21555600 at 23:31:20...
i: 21555700 at 23:31:20...
i: 21555800 at 23:31:20...
i

i: 21583300 at 23:31:25...
i: 21583400 at 23:31:25...
i: 21583500 at 23:31:25...
i: 21583600 at 23:31:25...
i: 21583700 at 23:31:25...
i: 21583800 at 23:31:25...
i: 21583900 at 23:31:25...
i: 21584000 at 23:31:25...
i: 21584100 at 23:31:25...
i: 21584200 at 23:31:25...
i: 21584300 at 23:31:25...
i: 21584400 at 23:31:25...
i: 21584500 at 23:31:25...
i: 21584600 at 23:31:25...
i: 21584700 at 23:31:25...
i: 21584800 at 23:31:25...
i: 21584900 at 23:31:25...
i: 21585000 at 23:31:26...
i: 21585100 at 23:31:26...
i: 21585200 at 23:31:26...
i: 21585300 at 23:31:26...
i: 21585400 at 23:31:26...
i: 21585500 at 23:31:26...
i: 21585600 at 23:31:26...
i: 21585700 at 23:31:26...
i: 21585800 at 23:31:26...
i: 21585900 at 23:31:26...
i: 21586000 at 23:31:26...
i: 21586100 at 23:31:26...
i: 21586200 at 23:31:26...
i: 21586300 at 23:31:26...
i: 21586400 at 23:31:26...
i: 21586500 at 23:31:26...
i: 21586600 at 23:31:26...
i: 21586700 at 23:31:26...
i: 21586800 at 23:31:26...
i: 21586900 at 23:31:26...
i

i: 21614600 at 23:31:32...
i: 21614700 at 23:31:32...
i: 21614800 at 23:31:32...
i: 21614900 at 23:31:32...
i: 21615000 at 23:31:32...
i: 21615100 at 23:31:32...
i: 21615200 at 23:31:32...
i: 21615300 at 23:31:32...
i: 21615400 at 23:31:32...
i: 21615500 at 23:31:32...
i: 21615600 at 23:31:32...
i: 21615700 at 23:31:32...
i: 21615800 at 23:31:32...
i: 21615900 at 23:31:32...
i: 21616000 at 23:31:32...
i: 21616100 at 23:31:32...
i: 21616200 at 23:31:32...
i: 21616300 at 23:31:32...
i: 21616400 at 23:31:32...
i: 21616500 at 23:31:32...
i: 21616600 at 23:31:32...
i: 21616700 at 23:31:32...
i: 21616800 at 23:31:32...
i: 21616900 at 23:31:32...
i: 21617000 at 23:31:32...
i: 21617100 at 23:31:32...
i: 21617200 at 23:31:32...
i: 21617300 at 23:31:32...
i: 21617400 at 23:31:32...
i: 21617500 at 23:31:32...
i: 21617600 at 23:31:32...
i: 21617700 at 23:31:32...
i: 21617800 at 23:31:32...
i: 21617900 at 23:31:32...
i: 21618000 at 23:31:32...
i: 21618100 at 23:31:32...
i: 21618200 at 23:31:32...
i

i: 21645500 at 23:31:38...
i: 21645600 at 23:31:38...
i: 21645700 at 23:31:38...
i: 21645800 at 23:31:38...
i: 21645900 at 23:31:38...
i: 21646000 at 23:31:38...
i: 21646100 at 23:31:38...
i: 21646200 at 23:31:38...
i: 21646300 at 23:31:38...
i: 21646400 at 23:31:38...
i: 21646500 at 23:31:38...
i: 21646600 at 23:31:38...
i: 21646700 at 23:31:38...
i: 21646800 at 23:31:38...
i: 21646900 at 23:31:38...
i: 21647000 at 23:31:38...
i: 21647100 at 23:31:38...
i: 21647200 at 23:31:38...
i: 21647300 at 23:31:38...
i: 21647400 at 23:31:38...
i: 21647500 at 23:31:38...
i: 21647600 at 23:31:38...
i: 21647700 at 23:31:38...
i: 21647800 at 23:31:38...
i: 21647900 at 23:31:38...
i: 21648000 at 23:31:38...
i: 21648100 at 23:31:38...
i: 21648200 at 23:31:38...
i: 21648300 at 23:31:38...
i: 21648400 at 23:31:39...
i: 21648500 at 23:31:39...
i: 21648600 at 23:31:39...
i: 21648700 at 23:31:39...
i: 21648800 at 23:31:39...
i: 21648900 at 23:31:39...
i: 21649000 at 23:31:39...
i: 21649100 at 23:31:39...
i

In [15]:
create_tif_map(scaled2020_th_band, "2020", features[0])

Start writing to tif image at 23:38:59...
Done writing to tif image at 23:39:01...


In [43]:
scaled2020_ru_band = create_tif_band(scaled2020_df, features[1])
print(scaled2020_ru_band.shape)

Start creating tif band at 00:26:03...
i: 0 at 00:26:03...
i: 10000 at 00:26:05...
i: 20000 at 00:26:07...
i: 30000 at 00:26:09...
i: 40000 at 00:26:11...
i: 50000 at 00:26:12...
i: 60000 at 00:26:14...
i: 70000 at 00:26:16...
i: 80000 at 00:26:18...
i: 90000 at 00:26:20...
i: 100000 at 00:26:22...
i: 110000 at 00:26:24...
i: 120000 at 00:26:25...
i: 130000 at 00:26:27...
i: 140000 at 00:26:29...
i: 150000 at 00:26:31...
i: 160000 at 00:26:32...
i: 170000 at 00:26:34...
i: 180000 at 00:26:36...
i: 190000 at 00:26:38...
i: 200000 at 00:26:39...
i: 210000 at 00:26:41...
i: 220000 at 00:26:43...
i: 230000 at 00:26:45...
i: 240000 at 00:26:46...
i: 250000 at 00:26:48...
i: 260000 at 00:26:50...
i: 270000 at 00:26:52...
i: 280000 at 00:26:53...
i: 290000 at 00:26:55...
i: 300000 at 00:26:57...
i: 310000 at 00:26:58...
i: 320000 at 00:27:00...
i: 330000 at 00:27:02...
i: 340000 at 00:27:04...
i: 350000 at 00:27:05...
i: 360000 at 00:27:07...
i: 370000 at 00:27:09...
i: 380000 at 00:27:11...


i: 3180000 at 00:36:28...
i: 3190000 at 00:36:30...
i: 3200000 at 00:36:32...
i: 3210000 at 00:36:34...
i: 3220000 at 00:36:36...
i: 3230000 at 00:36:37...
i: 3240000 at 00:36:39...
i: 3250000 at 00:36:41...
i: 3260000 at 00:36:43...
i: 3270000 at 00:36:45...
i: 3280000 at 00:36:48...
i: 3290000 at 00:36:52...
i: 3300000 at 00:36:55...
i: 3310000 at 00:36:58...
i: 3320000 at 00:37:01...
i: 3330000 at 00:37:03...
i: 3340000 at 00:37:05...
i: 3350000 at 00:37:07...
i: 3360000 at 00:37:09...
i: 3370000 at 00:37:11...
i: 3380000 at 00:37:14...
i: 3390000 at 00:37:16...
i: 3400000 at 00:37:18...
i: 3410000 at 00:37:20...
i: 3420000 at 00:37:22...
i: 3430000 at 00:37:24...
i: 3440000 at 00:37:26...
i: 3450000 at 00:37:28...
i: 3460000 at 00:37:31...
i: 3470000 at 00:37:33...
i: 3480000 at 00:37:35...
i: 3490000 at 00:37:37...
i: 3500000 at 00:37:39...
i: 3510000 at 00:37:41...
i: 3520000 at 00:37:43...
i: 3530000 at 00:37:45...
i: 3540000 at 00:37:47...
i: 3550000 at 00:37:49...
i: 3560000 a

i: 6340000 at 00:47:01...
i: 6350000 at 00:47:03...
i: 6360000 at 00:47:04...
i: 6370000 at 00:47:06...
i: 6380000 at 00:47:08...
i: 6390000 at 00:47:10...
i: 6400000 at 00:47:12...
i: 6410000 at 00:47:13...
i: 6420000 at 00:47:15...
i: 6430000 at 00:47:17...
i: 6440000 at 00:47:19...
i: 6450000 at 00:47:21...
i: 6460000 at 00:47:23...
i: 6470000 at 00:47:25...
i: 6480000 at 00:47:27...
i: 6490000 at 00:47:29...
i: 6500000 at 00:47:31...
i: 6510000 at 00:47:33...
i: 6520000 at 00:47:35...
i: 6530000 at 00:47:38...
i: 6540000 at 00:47:41...
i: 6550000 at 00:47:43...
i: 6560000 at 00:47:45...
i: 6570000 at 00:47:47...
i: 6580000 at 00:47:49...
i: 6590000 at 00:47:51...
i: 6600000 at 00:47:52...
i: 6610000 at 00:47:54...
i: 6620000 at 00:47:56...
i: 6630000 at 00:47:58...
i: 6640000 at 00:48:00...
i: 6650000 at 00:48:01...
i: 6660000 at 00:48:04...
i: 6670000 at 00:48:06...
i: 6680000 at 00:48:07...
i: 6690000 at 00:48:09...
i: 6700000 at 00:48:11...
i: 6710000 at 00:48:13...
i: 6720000 a

i: 9500000 at 00:57:20...
i: 9510000 at 00:57:22...
i: 9520000 at 00:57:24...
i: 9530000 at 00:57:25...
i: 9540000 at 00:57:27...
i: 9550000 at 00:57:29...
i: 9560000 at 00:57:31...
i: 9570000 at 00:57:33...
i: 9580000 at 00:57:34...
i: 9590000 at 00:57:36...
i: 9600000 at 00:57:38...
i: 9610000 at 00:57:40...
i: 9620000 at 00:57:42...
i: 9630000 at 00:57:44...
i: 9640000 at 00:57:45...
i: 9650000 at 00:57:47...
i: 9660000 at 00:57:50...
i: 9670000 at 00:57:52...
i: 9680000 at 00:57:54...
i: 9690000 at 00:57:56...
i: 9700000 at 00:57:58...
i: 9710000 at 00:58:00...
i: 9720000 at 00:58:02...
i: 9730000 at 00:58:04...
i: 9740000 at 00:58:06...
i: 9750000 at 00:58:08...
i: 9760000 at 00:58:09...
i: 9770000 at 00:58:11...
i: 9780000 at 00:58:13...
i: 9790000 at 00:58:15...
i: 9800000 at 00:58:16...
i: 9810000 at 00:58:18...
i: 9820000 at 00:58:20...
i: 9830000 at 00:58:22...
i: 9840000 at 00:58:24...
i: 9850000 at 00:58:25...
i: 9860000 at 00:58:27...
i: 9870000 at 00:58:29...
i: 9880000 a

i: 12560000 at 01:07:14...
i: 12570000 at 01:07:16...
i: 12580000 at 01:07:18...
i: 12590000 at 01:07:19...
i: 12600000 at 01:07:21...
i: 12610000 at 01:07:23...
i: 12620000 at 01:07:25...
i: 12630000 at 01:07:27...
i: 12640000 at 01:07:30...
i: 12650000 at 01:07:31...
i: 12660000 at 01:07:34...
i: 12670000 at 01:07:35...
i: 12680000 at 01:07:37...
i: 12690000 at 01:07:39...
i: 12700000 at 01:07:41...
i: 12710000 at 01:07:43...
i: 12720000 at 01:07:45...
i: 12730000 at 01:07:46...
i: 12740000 at 01:07:48...
i: 12750000 at 01:07:50...
i: 12760000 at 01:07:52...
i: 12770000 at 01:07:53...
i: 12780000 at 01:07:55...
i: 12790000 at 01:07:57...
i: 12800000 at 01:07:59...
i: 12810000 at 01:08:01...
i: 12820000 at 01:08:03...
i: 12830000 at 01:08:05...
i: 12840000 at 01:08:07...
i: 12850000 at 01:08:09...
i: 12860000 at 01:08:11...
i: 12870000 at 01:08:14...
i: 12880000 at 01:08:16...
i: 12890000 at 01:08:18...
i: 12900000 at 01:08:20...
i: 12910000 at 01:08:22...
i: 12920000 at 01:08:25...
i

i: 15600000 at 01:17:17...
i: 15610000 at 01:17:18...
i: 15620000 at 01:17:20...
i: 15630000 at 01:17:22...
i: 15640000 at 01:17:24...
i: 15650000 at 01:17:25...
i: 15660000 at 01:17:27...
i: 15670000 at 01:17:29...
i: 15680000 at 01:17:31...
i: 15690000 at 01:17:33...
i: 15700000 at 01:17:34...
i: 15710000 at 01:17:36...
i: 15720000 at 01:17:38...
i: 15730000 at 01:17:40...
i: 15740000 at 01:17:41...
i: 15750000 at 01:17:43...
i: 15760000 at 01:17:45...
i: 15770000 at 01:17:47...
i: 15780000 at 01:17:49...
i: 15790000 at 01:17:51...
i: 15800000 at 01:17:53...
i: 15810000 at 01:17:55...
i: 15820000 at 01:17:57...
i: 15830000 at 01:17:59...
i: 15840000 at 01:18:01...
i: 15850000 at 01:18:03...
i: 15860000 at 01:18:05...
i: 15870000 at 01:18:08...
i: 15880000 at 01:18:10...
i: 15890000 at 01:18:12...
i: 15900000 at 01:18:14...
i: 15910000 at 01:18:16...
i: 15920000 at 01:18:18...
i: 15930000 at 01:18:20...
i: 15940000 at 01:18:21...
i: 15950000 at 01:18:23...
i: 15960000 at 01:18:25...
i

i: 18640000 at 01:26:55...
i: 18650000 at 01:26:57...
i: 18660000 at 01:26:59...
i: 18670000 at 01:27:01...
i: 18680000 at 01:27:02...
i: 18690000 at 01:27:04...
i: 18700000 at 01:27:07...
i: 18710000 at 01:27:10...
i: 18720000 at 01:27:13...
i: 18730000 at 01:27:17...
i: 18740000 at 01:27:20...
i: 18750000 at 01:27:22...
i: 18760000 at 01:27:25...
i: 18770000 at 01:27:27...
i: 18780000 at 01:27:30...
i: 18790000 at 01:27:32...
i: 18800000 at 01:27:34...
i: 18810000 at 01:27:36...
i: 18820000 at 01:27:38...
i: 18830000 at 01:27:40...
i: 18840000 at 01:27:42...
i: 18850000 at 01:27:45...
i: 18860000 at 01:27:47...
i: 18870000 at 01:27:48...
i: 18880000 at 01:27:50...
i: 18890000 at 01:27:52...
i: 18900000 at 01:27:54...
i: 18910000 at 01:27:56...
i: 18920000 at 01:27:58...
i: 18930000 at 01:27:59...
i: 18940000 at 01:28:01...
i: 18950000 at 01:28:03...
i: 18960000 at 01:28:06...
i: 18970000 at 01:28:08...
i: 18980000 at 01:28:10...
i: 18990000 at 01:28:12...
i: 19000000 at 01:28:14...
i

In [44]:
scaled2020_fb_band = create_tif_band(scaled2020_df, features[2])
print(scaled2020_fb_band.shape)

Start creating tif band at 01:36:50...
i: 0 at 01:36:50...
i: 10000 at 01:36:52...
i: 20000 at 01:36:53...
i: 30000 at 01:36:55...
i: 40000 at 01:36:57...
i: 50000 at 01:36:59...
i: 60000 at 01:37:01...
i: 70000 at 01:37:03...
i: 80000 at 01:37:04...
i: 90000 at 01:37:06...
i: 100000 at 01:37:08...
i: 110000 at 01:37:10...
i: 120000 at 01:37:12...
i: 130000 at 01:37:13...
i: 140000 at 01:37:15...
i: 150000 at 01:37:17...
i: 160000 at 01:37:19...
i: 170000 at 01:37:21...
i: 180000 at 01:37:23...
i: 190000 at 01:37:25...
i: 200000 at 01:37:27...
i: 210000 at 01:37:29...
i: 220000 at 01:37:31...
i: 230000 at 01:37:33...
i: 240000 at 01:37:34...
i: 250000 at 01:37:36...
i: 260000 at 01:37:38...
i: 270000 at 01:37:40...
i: 280000 at 01:37:42...
i: 290000 at 01:37:43...
i: 300000 at 01:37:45...
i: 310000 at 01:37:47...
i: 320000 at 01:37:49...
i: 330000 at 01:37:50...
i: 340000 at 01:37:52...
i: 350000 at 01:37:54...
i: 360000 at 01:37:56...
i: 370000 at 01:37:58...
i: 380000 at 01:37:59...


i: 3180000 at 01:46:49...
i: 3190000 at 01:46:52...
i: 3200000 at 01:46:54...
i: 3210000 at 01:46:56...
i: 3220000 at 01:46:58...
i: 3230000 at 01:47:00...
i: 3240000 at 01:47:01...
i: 3250000 at 01:47:03...
i: 3260000 at 01:47:05...
i: 3270000 at 01:47:07...
i: 3280000 at 01:47:09...
i: 3290000 at 01:47:10...
i: 3300000 at 01:47:12...
i: 3310000 at 01:47:14...
i: 3320000 at 01:47:16...
i: 3330000 at 01:47:17...
i: 3340000 at 01:47:19...
i: 3350000 at 01:47:21...
i: 3360000 at 01:47:23...
i: 3370000 at 01:47:24...
i: 3380000 at 01:47:27...
i: 3390000 at 01:47:29...
i: 3400000 at 01:47:30...
i: 3410000 at 01:47:32...
i: 3420000 at 01:47:35...
i: 3430000 at 01:47:36...
i: 3440000 at 01:47:38...
i: 3450000 at 01:47:40...
i: 3460000 at 01:47:42...
i: 3470000 at 01:47:44...
i: 3480000 at 01:47:45...
i: 3490000 at 01:47:47...
i: 3500000 at 01:47:49...
i: 3510000 at 01:47:51...
i: 3520000 at 01:47:52...
i: 3530000 at 01:47:54...
i: 3540000 at 01:47:56...
i: 3550000 at 01:47:58...
i: 3560000 a

i: 6340000 at 01:56:39...
i: 6350000 at 01:56:41...
i: 6360000 at 01:56:43...
i: 6370000 at 01:56:44...
i: 6380000 at 01:56:46...
i: 6390000 at 01:56:48...
i: 6400000 at 01:56:50...
i: 6410000 at 01:56:51...
i: 6420000 at 01:56:53...
i: 6430000 at 01:56:55...
i: 6440000 at 01:56:57...
i: 6450000 at 01:56:58...
i: 6460000 at 01:57:00...
i: 6470000 at 01:57:02...
i: 6480000 at 01:57:04...
i: 6490000 at 01:57:05...
i: 6500000 at 01:57:07...
i: 6510000 at 01:57:09...
i: 6520000 at 01:57:11...
i: 6530000 at 01:57:12...
i: 6540000 at 01:57:14...
i: 6550000 at 01:57:16...
i: 6560000 at 01:57:18...
i: 6570000 at 01:57:19...
i: 6580000 at 01:57:21...
i: 6590000 at 01:57:23...
i: 6600000 at 01:57:25...
i: 6610000 at 01:57:26...
i: 6620000 at 01:57:28...
i: 6630000 at 01:57:30...
i: 6640000 at 01:57:32...
i: 6650000 at 01:57:34...
i: 6660000 at 01:57:35...
i: 6670000 at 01:57:37...
i: 6680000 at 01:57:39...
i: 6690000 at 01:57:41...
i: 6700000 at 01:57:43...
i: 6710000 at 01:57:44...
i: 6720000 a

i: 9500000 at 02:06:45...
i: 9510000 at 02:06:47...
i: 9520000 at 02:06:49...
i: 9530000 at 02:06:51...
i: 9540000 at 02:06:54...
i: 9550000 at 02:06:56...
i: 9560000 at 02:06:59...
i: 9570000 at 02:07:03...
i: 9580000 at 02:07:08...
i: 9590000 at 02:07:10...
i: 9600000 at 02:07:12...
i: 9610000 at 02:07:14...
i: 9620000 at 02:07:17...
i: 9630000 at 02:07:19...
i: 9640000 at 02:07:21...
i: 9650000 at 02:07:23...
i: 9660000 at 02:07:25...
i: 9670000 at 02:07:27...
i: 9680000 at 02:07:29...
i: 9690000 at 02:07:31...
i: 9700000 at 02:07:33...
i: 9710000 at 02:07:35...
i: 9720000 at 02:07:37...
i: 9730000 at 02:07:39...
i: 9740000 at 02:07:41...
i: 9750000 at 02:07:43...
i: 9760000 at 02:07:45...
i: 9770000 at 02:07:47...
i: 9780000 at 02:07:49...
i: 9790000 at 02:07:51...
i: 9800000 at 02:07:56...
i: 9810000 at 02:07:59...
i: 9820000 at 02:08:01...
i: 9830000 at 02:08:02...
i: 9840000 at 02:08:04...
i: 9850000 at 02:08:06...
i: 9860000 at 02:08:08...
i: 9870000 at 02:08:09...
i: 9880000 a

i: 12560000 at 02:16:37...
i: 12570000 at 02:16:39...
i: 12580000 at 02:16:41...
i: 12590000 at 02:16:43...
i: 12600000 at 02:16:45...
i: 12610000 at 02:16:46...
i: 12620000 at 02:16:48...
i: 12630000 at 02:16:50...
i: 12640000 at 02:16:52...
i: 12650000 at 02:16:54...
i: 12660000 at 02:16:56...
i: 12670000 at 02:16:57...
i: 12680000 at 02:16:59...
i: 12690000 at 02:17:01...
i: 12700000 at 02:17:03...
i: 12710000 at 02:17:05...
i: 12720000 at 02:17:07...
i: 12730000 at 02:17:09...
i: 12740000 at 02:17:11...
i: 12750000 at 02:17:12...
i: 12760000 at 02:17:14...
i: 12770000 at 02:17:16...
i: 12780000 at 02:17:18...
i: 12790000 at 02:17:20...
i: 12800000 at 02:17:22...
i: 12810000 at 02:17:23...
i: 12820000 at 02:17:25...
i: 12830000 at 02:17:27...
i: 12840000 at 02:17:29...
i: 12850000 at 02:17:31...
i: 12860000 at 02:17:33...
i: 12870000 at 02:17:34...
i: 12880000 at 02:17:36...
i: 12890000 at 02:17:38...
i: 12900000 at 02:17:40...
i: 12910000 at 02:17:42...
i: 12920000 at 02:17:43...
i

i: 15600000 at 02:26:29...
i: 15610000 at 02:26:31...
i: 15620000 at 02:26:33...
i: 15630000 at 02:26:34...
i: 15640000 at 02:26:36...
i: 15650000 at 02:26:39...
i: 15660000 at 02:26:41...
i: 15670000 at 02:26:44...
i: 15680000 at 02:26:46...
i: 15690000 at 02:26:48...
i: 15700000 at 02:26:50...
i: 15710000 at 02:26:52...
i: 15720000 at 02:26:54...
i: 15730000 at 02:26:56...
i: 15740000 at 02:26:58...
i: 15750000 at 02:27:00...
i: 15760000 at 02:27:01...
i: 15770000 at 02:27:03...
i: 15780000 at 02:27:06...
i: 15790000 at 02:27:08...
i: 15800000 at 02:27:10...
i: 15810000 at 02:27:11...
i: 15820000 at 02:27:13...
i: 15830000 at 02:27:15...
i: 15840000 at 02:27:17...
i: 15850000 at 02:27:19...
i: 15860000 at 02:27:21...
i: 15870000 at 02:27:22...
i: 15880000 at 02:27:24...
i: 15890000 at 02:27:26...
i: 15900000 at 02:27:28...
i: 15910000 at 02:27:30...
i: 15920000 at 02:27:33...
i: 15930000 at 02:27:35...
i: 15940000 at 02:27:37...
i: 15950000 at 02:27:39...
i: 15960000 at 02:27:41...
i

i: 18640000 at 02:36:15...
i: 18650000 at 02:36:16...
i: 18660000 at 02:36:18...
i: 18670000 at 02:36:20...
i: 18680000 at 02:36:21...
i: 18690000 at 02:36:23...
i: 18700000 at 02:36:25...
i: 18710000 at 02:36:27...
i: 18720000 at 02:36:28...
i: 18730000 at 02:36:30...
i: 18740000 at 02:36:32...
i: 18750000 at 02:36:34...
i: 18760000 at 02:36:35...
i: 18770000 at 02:36:37...
i: 18780000 at 02:36:39...
i: 18790000 at 02:36:41...
i: 18800000 at 02:36:42...
i: 18810000 at 02:36:44...
i: 18820000 at 02:36:46...
i: 18830000 at 02:36:48...
i: 18840000 at 02:36:49...
i: 18850000 at 02:36:51...
i: 18860000 at 02:36:53...
i: 18870000 at 02:36:55...
i: 18880000 at 02:36:56...
i: 18890000 at 02:36:58...
i: 18900000 at 02:37:00...
i: 18910000 at 02:37:01...
i: 18920000 at 02:37:03...
i: 18930000 at 02:37:05...
i: 18940000 at 02:37:07...
i: 18950000 at 02:37:08...
i: 18960000 at 02:37:10...
i: 18970000 at 02:37:12...
i: 18980000 at 02:37:14...
i: 18990000 at 02:37:15...
i: 19000000 at 02:37:17...
i

In [45]:
create_tif_map(scaled2020_ru_band, "2020", features[1])

Start writing to tif image at 02:45:01...
Done writing to tif image at 02:45:03...


In [46]:
create_tif_map(scaled2020_fb_band, "2020", features[2])

Start writing to tif image at 02:45:03...
Done writing to tif image at 02:45:06...


In [28]:
scaled2025_df = pd.read_pickle("results/scaled2025.pkl")
scaled2025_df

y     x       lat         lon  prophet
0         5801     0  7.675769  116.041573      NaN
1         5802     0  7.673269  116.041573      NaN
2         5803     0  7.670769  116.041573      NaN
3         5804     0  7.668269  116.041573      NaN
4         5805     0  7.665769  116.041573      NaN
...        ...   ...       ...         ...      ...
22423447  5957  4950  7.285769  128.416580      NaN
22423448  5958  4950  7.283269  128.416580      NaN
22423449  5959  4950  7.280769  128.416580      NaN
22423450  5960  4950  7.278269  128.416580      NaN
22423451  5961  4950  7.275769  128.416580      NaN

[22423452 rows x 5 columns]

In [29]:
scaled2025_band = create_tif_band(scaled2025_df, "prophet")
print(scaled2025_band.shape)

Start creating tif band at 03:09:34...
i: 0 at 03:09:34...
i: 10000 at 03:09:36...
i: 20000 at 03:09:38...
i: 30000 at 03:09:40...
i: 40000 at 03:09:42...
i: 50000 at 03:09:44...
i: 60000 at 03:09:46...
i: 70000 at 03:09:48...
i: 80000 at 03:09:50...
i: 90000 at 03:09:52...
i: 100000 at 03:09:54...
i: 110000 at 03:09:56...
i: 120000 at 03:09:57...
i: 130000 at 03:09:59...
i: 140000 at 03:10:01...
i: 150000 at 03:10:03...
i: 160000 at 03:10:05...
i: 170000 at 03:10:07...
i: 180000 at 03:10:09...
i: 190000 at 03:10:11...
i: 200000 at 03:10:14...
i: 210000 at 03:10:16...
i: 220000 at 03:10:19...
i: 230000 at 03:10:22...
i: 240000 at 03:10:24...
i: 250000 at 03:10:26...
i: 260000 at 03:10:28...
i: 270000 at 03:10:30...
i: 280000 at 03:10:32...
i: 290000 at 03:10:34...
i: 300000 at 03:10:36...
i: 310000 at 03:10:38...
i: 320000 at 03:10:40...
i: 330000 at 03:10:42...
i: 340000 at 03:10:44...
i: 350000 at 03:10:46...
i: 360000 at 03:10:48...
i: 370000 at 03:10:50...
i: 380000 at 03:10:53...


i: 3180000 at 03:19:34...
i: 3190000 at 03:19:36...
i: 3200000 at 03:19:39...
i: 3210000 at 03:19:41...
i: 3220000 at 03:19:43...
i: 3230000 at 03:19:45...
i: 3240000 at 03:19:48...
i: 3250000 at 03:19:50...
i: 3260000 at 03:19:52...
i: 3270000 at 03:19:54...
i: 3280000 at 03:19:56...
i: 3290000 at 03:19:58...
i: 3300000 at 03:20:00...
i: 3310000 at 03:20:02...
i: 3320000 at 03:20:04...
i: 3330000 at 03:20:06...
i: 3340000 at 03:20:08...
i: 3350000 at 03:20:10...
i: 3360000 at 03:20:12...
i: 3370000 at 03:20:14...
i: 3380000 at 03:20:16...
i: 3390000 at 03:20:18...
i: 3400000 at 03:20:20...
i: 3410000 at 03:20:22...
i: 3420000 at 03:20:24...
i: 3430000 at 03:20:26...
i: 3440000 at 03:20:28...
i: 3450000 at 03:20:30...
i: 3460000 at 03:20:32...
i: 3470000 at 03:20:34...
i: 3480000 at 03:20:36...
i: 3490000 at 03:20:38...
i: 3500000 at 03:20:39...
i: 3510000 at 03:20:41...
i: 3520000 at 03:20:43...
i: 3530000 at 03:20:46...
i: 3540000 at 03:20:48...
i: 3550000 at 03:20:50...
i: 3560000 a

i: 6340000 at 03:31:19...
i: 6350000 at 03:31:23...
i: 6360000 at 03:31:26...
i: 6370000 at 03:31:29...
i: 6380000 at 03:31:32...
i: 6390000 at 03:31:34...
i: 6400000 at 03:31:36...
i: 6410000 at 03:31:39...
i: 6420000 at 03:31:41...
i: 6430000 at 03:31:44...
i: 6440000 at 03:31:46...
i: 6450000 at 03:31:48...
i: 6460000 at 03:31:51...
i: 6470000 at 03:31:53...
i: 6480000 at 03:31:56...
i: 6490000 at 03:31:58...
i: 6500000 at 03:32:00...
i: 6510000 at 03:32:03...
i: 6520000 at 03:32:05...
i: 6530000 at 03:32:08...
i: 6540000 at 03:32:10...
i: 6550000 at 03:32:13...
i: 6560000 at 03:32:15...
i: 6570000 at 03:32:17...
i: 6580000 at 03:32:20...
i: 6590000 at 03:32:22...
i: 6600000 at 03:32:24...
i: 6610000 at 03:32:27...
i: 6620000 at 03:32:29...
i: 6630000 at 03:32:32...
i: 6640000 at 03:32:34...
i: 6650000 at 03:32:36...
i: 6660000 at 03:32:39...
i: 6670000 at 03:32:41...
i: 6680000 at 03:32:44...
i: 6690000 at 03:32:46...
i: 6700000 at 03:32:49...
i: 6710000 at 03:32:51...
i: 6720000 a

i: 9500000 at 03:45:51...
i: 9510000 at 03:45:54...
i: 9520000 at 03:45:57...
i: 9530000 at 03:45:59...
i: 9540000 at 03:46:02...
i: 9550000 at 03:46:05...
i: 9560000 at 03:46:08...
i: 9570000 at 03:46:11...
i: 9580000 at 03:46:14...
i: 9590000 at 03:46:18...
i: 9600000 at 03:46:21...
i: 9610000 at 03:46:24...
i: 9620000 at 03:46:27...
i: 9630000 at 03:46:31...
i: 9640000 at 03:46:35...
i: 9650000 at 03:46:38...
i: 9660000 at 03:46:42...
i: 9670000 at 03:46:45...
i: 9680000 at 03:46:49...
i: 9690000 at 03:46:52...
i: 9700000 at 03:46:55...
i: 9710000 at 03:46:59...
i: 9720000 at 03:47:02...
i: 9730000 at 03:47:05...
i: 9740000 at 03:47:08...
i: 9750000 at 03:47:12...
i: 9760000 at 03:47:16...
i: 9770000 at 03:47:19...
i: 9780000 at 03:47:22...
i: 9790000 at 03:47:24...
i: 9800000 at 03:47:27...
i: 9810000 at 03:47:29...
i: 9820000 at 03:47:32...
i: 9830000 at 03:47:35...
i: 9840000 at 03:47:37...
i: 9850000 at 03:47:40...
i: 9860000 at 03:47:44...
i: 9870000 at 03:47:47...
i: 9880000 a

i: 12560000 at 03:59:38...
i: 12570000 at 03:59:41...
i: 12580000 at 03:59:43...
i: 12590000 at 03:59:45...
i: 12600000 at 03:59:48...
i: 12610000 at 03:59:50...
i: 12620000 at 03:59:52...
i: 12630000 at 03:59:55...
i: 12640000 at 03:59:57...
i: 12650000 at 03:59:59...
i: 12660000 at 04:00:02...
i: 12670000 at 04:00:04...
i: 12680000 at 04:00:06...
i: 12690000 at 04:00:09...
i: 12700000 at 04:00:12...
i: 12710000 at 04:00:15...
i: 12720000 at 04:00:17...
i: 12730000 at 04:00:19...
i: 12740000 at 04:00:22...
i: 12750000 at 04:00:24...
i: 12760000 at 04:00:26...
i: 12770000 at 04:00:29...
i: 12780000 at 04:00:31...
i: 12790000 at 04:00:33...
i: 12800000 at 04:00:36...
i: 12810000 at 04:00:38...
i: 12820000 at 04:00:40...
i: 12830000 at 04:00:43...
i: 12840000 at 04:00:45...
i: 12850000 at 04:00:48...
i: 12860000 at 04:00:50...
i: 12870000 at 04:00:53...
i: 12880000 at 04:00:55...
i: 12890000 at 04:00:57...
i: 12900000 at 04:00:59...
i: 12910000 at 04:01:02...
i: 12920000 at 04:01:04...
i

i: 15600000 at 04:11:40...
i: 15610000 at 04:11:42...
i: 15620000 at 04:11:44...
i: 15630000 at 04:11:46...
i: 15640000 at 04:11:49...
i: 15650000 at 04:11:51...
i: 15660000 at 04:11:53...
i: 15670000 at 04:11:56...
i: 15680000 at 04:11:58...
i: 15690000 at 04:12:00...
i: 15700000 at 04:12:03...
i: 15710000 at 04:12:05...
i: 15720000 at 04:12:08...
i: 15730000 at 04:12:10...
i: 15740000 at 04:12:12...
i: 15750000 at 04:12:15...
i: 15760000 at 04:12:17...
i: 15770000 at 04:12:19...
i: 15780000 at 04:12:22...
i: 15790000 at 04:12:24...
i: 15800000 at 04:12:26...
i: 15810000 at 04:12:29...
i: 15820000 at 04:12:31...
i: 15830000 at 04:12:33...
i: 15840000 at 04:12:36...
i: 15850000 at 04:12:38...
i: 15860000 at 04:12:40...
i: 15870000 at 04:12:43...
i: 15880000 at 04:12:45...
i: 15890000 at 04:12:47...
i: 15900000 at 04:12:50...
i: 15910000 at 04:12:52...
i: 15920000 at 04:12:54...
i: 15930000 at 04:12:57...
i: 15940000 at 04:12:59...
i: 15950000 at 04:13:01...
i: 15960000 at 04:13:04...
i

i: 18640000 at 04:23:40...
i: 18650000 at 04:23:42...
i: 18660000 at 04:23:44...
i: 18670000 at 04:23:45...
i: 18680000 at 04:23:47...
i: 18690000 at 04:23:49...
i: 18700000 at 04:23:51...
i: 18710000 at 04:23:52...
i: 18720000 at 04:23:54...
i: 18730000 at 04:23:56...
i: 18740000 at 04:23:58...
i: 18750000 at 04:24:00...
i: 18760000 at 04:24:01...
i: 18770000 at 04:24:03...
i: 18780000 at 04:24:05...
i: 18790000 at 04:24:07...
i: 18800000 at 04:24:08...
i: 18810000 at 04:24:10...
i: 18820000 at 04:24:12...
i: 18830000 at 04:24:13...
i: 18840000 at 04:24:15...
i: 18850000 at 04:24:17...
i: 18860000 at 04:24:19...
i: 18870000 at 04:24:20...
i: 18880000 at 04:24:22...
i: 18890000 at 04:24:24...
i: 18900000 at 04:24:26...
i: 18910000 at 04:24:27...
i: 18920000 at 04:24:29...
i: 18930000 at 04:24:31...
i: 18940000 at 04:24:33...
i: 18950000 at 04:24:34...
i: 18960000 at 04:24:36...
i: 18970000 at 04:24:38...
i: 18980000 at 04:24:40...
i: 18990000 at 04:24:41...
i: 19000000 at 04:24:43...
i

i: 21680000 at 04:32:30...
i: 21690000 at 04:32:31...
i: 21700000 at 04:32:33...
i: 21710000 at 04:32:35...
i: 21720000 at 04:32:37...
i: 21730000 at 04:32:39...
i: 21740000 at 04:32:40...
i: 21750000 at 04:32:42...
i: 21760000 at 04:32:44...
i: 21770000 at 04:32:45...
i: 21780000 at 04:32:47...
i: 21790000 at 04:32:49...
i: 21800000 at 04:32:51...
i: 21810000 at 04:32:52...
i: 21820000 at 04:32:54...
i: 21830000 at 04:32:56...
i: 21840000 at 04:32:58...
i: 21850000 at 04:32:59...
i: 21860000 at 04:33:01...
i: 21870000 at 04:33:03...
i: 21880000 at 04:33:04...
i: 21890000 at 04:33:06...
i: 21900000 at 04:33:08...
i: 21910000 at 04:33:10...
i: 21920000 at 04:33:11...
i: 21930000 at 04:33:13...
i: 21940000 at 04:33:15...
i: 21950000 at 04:33:17...
i: 21960000 at 04:33:19...
i: 21970000 at 04:33:20...
i: 21980000 at 04:33:22...
i: 21990000 at 04:33:24...
i: 22000000 at 04:33:26...
i: 22010000 at 04:33:27...
i: 22020000 at 04:33:29...
i: 22030000 at 04:33:31...
i: 22040000 at 04:33:33...
i

In [30]:
scaled2020_flat_df = pd.read_pickle("results/scaled2020_flat.pkl")
scaled2020_flat_df

y     x       lat         lon  windvelo  mean_wv  prophet  \
0         5801     0  7.675769  116.041573       NaN      NaN      NaN   
1         5802     0  7.673269  116.041573       NaN      NaN      NaN   
2         5803     0  7.670769  116.041573       NaN      NaN      NaN   
3         5804     0  7.668269  116.041573       NaN      NaN      NaN   
4         5805     0  7.665769  116.041573       NaN      NaN      NaN   
...        ...   ...       ...         ...       ...      ...      ...   
22423447  5957  4950  7.285769  128.416580       NaN      NaN      NaN   
22423448  5958  4950  7.283269  128.416580       NaN      NaN      NaN   
22423449  5959  4950  7.280769  128.416580       NaN      NaN      NaN   
22423450  5960  4950  7.278269  128.416580       NaN      NaN      NaN   
22423451  5961  4950  7.275769  128.416580       NaN      NaN      NaN   

          prophet_rmse  lstm_tanh  lstm_tanh_rmse  
0                  NaN        NaN             NaN  
1                  NaN        NaN             NaN  
2                  NaN        NaN             NaN  
3                  NaN        NaN             NaN  
4                  NaN        NaN             NaN  
...                ...        ...             ...  
22423447           NaN        NaN             NaN  
22423448           NaN        NaN             NaN  
22423449           NaN        NaN             NaN  
22423450           NaN        NaN             NaN  
22423451           NaN        NaN             NaN  

[22423452 rows x 10 columns]

In [31]:
scaled2020_wv_band = create_tif_band(scaled2020_flat_df, "mean_wv")
print(scaled2020_wv_band.shape)

Start creating tif band at 04:34:40...
i: 0 at 04:34:41...
i: 10000 at 04:34:42...
i: 20000 at 04:34:44...
i: 30000 at 04:34:46...
i: 40000 at 04:34:48...
i: 50000 at 04:34:49...
i: 60000 at 04:34:51...
i: 70000 at 04:34:53...
i: 80000 at 04:34:55...
i: 90000 at 04:34:56...
i: 100000 at 04:34:58...
i: 110000 at 04:35:00...
i: 120000 at 04:35:02...
i: 130000 at 04:35:03...
i: 140000 at 04:35:05...
i: 150000 at 04:35:07...
i: 160000 at 04:35:08...
i: 170000 at 04:35:10...
i: 180000 at 04:35:12...
i: 190000 at 04:35:14...
i: 200000 at 04:35:16...
i: 210000 at 04:35:18...
i: 220000 at 04:35:19...
i: 230000 at 04:35:21...
i: 240000 at 04:35:23...
i: 250000 at 04:35:25...
i: 260000 at 04:35:26...
i: 270000 at 04:35:28...
i: 280000 at 04:35:30...
i: 290000 at 04:35:31...
i: 300000 at 04:35:33...
i: 310000 at 04:35:35...
i: 320000 at 04:35:36...
i: 330000 at 04:35:38...
i: 340000 at 04:35:40...
i: 350000 at 04:35:42...
i: 360000 at 04:35:43...
i: 370000 at 04:35:45...
i: 380000 at 04:35:47...


i: 3180000 at 04:43:44...
i: 3190000 at 04:43:46...
i: 3200000 at 04:43:48...
i: 3210000 at 04:43:49...
i: 3220000 at 04:43:51...
i: 3230000 at 04:43:53...
i: 3240000 at 04:43:54...
i: 3250000 at 04:43:56...
i: 3260000 at 04:43:58...
i: 3270000 at 04:44:00...
i: 3280000 at 04:44:01...
i: 3290000 at 04:44:03...
i: 3300000 at 04:44:05...
i: 3310000 at 04:44:06...
i: 3320000 at 04:44:08...
i: 3330000 at 04:44:10...
i: 3340000 at 04:44:12...
i: 3350000 at 04:44:13...
i: 3360000 at 04:44:15...
i: 3370000 at 04:44:17...
i: 3380000 at 04:44:18...
i: 3390000 at 04:44:20...
i: 3400000 at 04:44:22...
i: 3410000 at 04:44:24...
i: 3420000 at 04:44:25...
i: 3430000 at 04:44:27...
i: 3440000 at 04:44:29...
i: 3450000 at 04:44:30...
i: 3460000 at 04:44:32...
i: 3470000 at 04:44:34...
i: 3480000 at 04:44:35...
i: 3490000 at 04:44:37...
i: 3500000 at 04:44:39...
i: 3510000 at 04:44:41...
i: 3520000 at 04:44:42...
i: 3530000 at 04:44:44...
i: 3540000 at 04:44:46...
i: 3550000 at 04:44:47...
i: 3560000 a

i: 6340000 at 04:52:44...
i: 6350000 at 04:52:46...
i: 6360000 at 04:52:47...
i: 6370000 at 04:52:49...
i: 6380000 at 04:52:51...
i: 6390000 at 04:52:52...
i: 6400000 at 04:52:54...
i: 6410000 at 04:52:56...
i: 6420000 at 04:52:58...
i: 6430000 at 04:52:59...
i: 6440000 at 04:53:01...
i: 6450000 at 04:53:03...
i: 6460000 at 04:53:04...
i: 6470000 at 04:53:06...
i: 6480000 at 04:53:08...
i: 6490000 at 04:53:09...
i: 6500000 at 04:53:11...
i: 6510000 at 04:53:13...
i: 6520000 at 04:53:15...
i: 6530000 at 04:53:16...
i: 6540000 at 04:53:18...
i: 6550000 at 04:53:20...
i: 6560000 at 04:53:22...
i: 6570000 at 04:53:23...
i: 6580000 at 04:53:25...
i: 6590000 at 04:53:27...
i: 6600000 at 04:53:28...
i: 6610000 at 04:53:30...
i: 6620000 at 04:53:32...
i: 6630000 at 04:53:33...
i: 6640000 at 04:53:35...
i: 6650000 at 04:53:37...
i: 6660000 at 04:53:39...
i: 6670000 at 04:53:40...
i: 6680000 at 04:53:42...
i: 6690000 at 04:53:44...
i: 6700000 at 04:53:45...
i: 6710000 at 04:53:47...
i: 6720000 a

i: 9500000 at 05:01:43...
i: 9510000 at 05:01:45...
i: 9520000 at 05:01:47...
i: 9530000 at 05:01:49...
i: 9540000 at 05:01:50...
i: 9550000 at 05:01:52...
i: 9560000 at 05:01:54...
i: 9570000 at 05:01:55...
i: 9580000 at 05:01:57...
i: 9590000 at 05:01:59...
i: 9600000 at 05:02:00...
i: 9610000 at 05:02:02...
i: 9620000 at 05:02:04...
i: 9630000 at 05:02:06...
i: 9640000 at 05:02:07...
i: 9650000 at 05:02:09...
i: 9660000 at 05:02:11...
i: 9670000 at 05:02:12...
i: 9680000 at 05:02:14...
i: 9690000 at 05:02:16...
i: 9700000 at 05:02:17...
i: 9710000 at 05:02:19...
i: 9720000 at 05:02:21...
i: 9730000 at 05:02:23...
i: 9740000 at 05:02:24...
i: 9750000 at 05:02:26...
i: 9760000 at 05:02:28...
i: 9770000 at 05:02:29...
i: 9780000 at 05:02:31...
i: 9790000 at 05:02:33...
i: 9800000 at 05:02:35...
i: 9810000 at 05:02:36...
i: 9820000 at 05:02:38...
i: 9830000 at 05:02:40...
i: 9840000 at 05:02:41...
i: 9850000 at 05:02:43...
i: 9860000 at 05:02:45...
i: 9870000 at 05:02:46...
i: 9880000 a

i: 12560000 at 05:10:25...
i: 12570000 at 05:10:27...
i: 12580000 at 05:10:29...
i: 12590000 at 05:10:30...
i: 12600000 at 05:10:32...
i: 12610000 at 05:10:34...
i: 12620000 at 05:10:36...
i: 12630000 at 05:10:37...
i: 12640000 at 05:10:39...
i: 12650000 at 05:10:41...
i: 12660000 at 05:10:42...
i: 12670000 at 05:10:44...
i: 12680000 at 05:10:46...
i: 12690000 at 05:10:47...
i: 12700000 at 05:10:49...
i: 12710000 at 05:10:51...
i: 12720000 at 05:10:53...
i: 12730000 at 05:10:54...
i: 12740000 at 05:10:56...
i: 12750000 at 05:10:58...
i: 12760000 at 05:10:59...
i: 12770000 at 05:11:01...
i: 12780000 at 05:11:03...
i: 12790000 at 05:11:04...
i: 12800000 at 05:11:06...
i: 12810000 at 05:11:08...
i: 12820000 at 05:11:10...
i: 12830000 at 05:11:11...
i: 12840000 at 05:11:13...
i: 12850000 at 05:11:15...
i: 12860000 at 05:11:16...
i: 12870000 at 05:11:18...
i: 12880000 at 05:11:20...
i: 12890000 at 05:11:21...
i: 12900000 at 05:11:23...
i: 12910000 at 05:11:25...
i: 12920000 at 05:11:27...
i

i: 15600000 at 05:19:05...
i: 15610000 at 05:19:06...
i: 15620000 at 05:19:08...
i: 15630000 at 05:19:10...
i: 15640000 at 05:19:11...
i: 15650000 at 05:19:13...
i: 15660000 at 05:19:15...
i: 15670000 at 05:19:17...
i: 15680000 at 05:19:18...
i: 15690000 at 05:19:20...
i: 15700000 at 05:19:22...
i: 15710000 at 05:19:23...
i: 15720000 at 05:19:25...
i: 15730000 at 05:19:27...
i: 15740000 at 05:19:29...
i: 15750000 at 05:19:30...
i: 15760000 at 05:19:32...
i: 15770000 at 05:19:34...
i: 15780000 at 05:19:35...
i: 15790000 at 05:19:37...
i: 15800000 at 05:19:39...
i: 15810000 at 05:19:40...
i: 15820000 at 05:19:42...
i: 15830000 at 05:19:44...
i: 15840000 at 05:19:46...
i: 15850000 at 05:19:47...
i: 15860000 at 05:19:49...
i: 15870000 at 05:19:51...
i: 15880000 at 05:19:52...
i: 15890000 at 05:19:54...
i: 15900000 at 05:19:56...
i: 15910000 at 05:19:57...
i: 15920000 at 05:19:59...
i: 15930000 at 05:20:01...
i: 15940000 at 05:20:03...
i: 15950000 at 05:20:04...
i: 15960000 at 05:20:06...
i

i: 18640000 at 05:27:45...
i: 18650000 at 05:27:47...
i: 18660000 at 05:27:48...
i: 18670000 at 05:27:50...
i: 18680000 at 05:27:52...
i: 18690000 at 05:27:53...
i: 18700000 at 05:27:55...
i: 18710000 at 05:27:57...
i: 18720000 at 05:27:58...
i: 18730000 at 05:28:00...
i: 18740000 at 05:28:02...
i: 18750000 at 05:28:04...
i: 18760000 at 05:28:05...
i: 18770000 at 05:28:07...
i: 18780000 at 05:28:09...
i: 18790000 at 05:28:10...
i: 18800000 at 05:28:12...
i: 18810000 at 05:28:14...
i: 18820000 at 05:28:16...
i: 18830000 at 05:28:17...
i: 18840000 at 05:28:19...
i: 18850000 at 05:28:21...
i: 18860000 at 05:28:22...
i: 18870000 at 05:28:24...
i: 18880000 at 05:28:26...
i: 18890000 at 05:28:27...
i: 18900000 at 05:28:29...
i: 18910000 at 05:28:31...
i: 18920000 at 05:28:33...
i: 18930000 at 05:28:34...
i: 18940000 at 05:28:36...
i: 18950000 at 05:28:38...
i: 18960000 at 05:28:39...
i: 18970000 at 05:28:41...
i: 18980000 at 05:28:43...
i: 18990000 at 05:28:44...
i: 19000000 at 05:28:46...
i

i: 21680000 at 05:36:25...
i: 21690000 at 05:36:27...
i: 21700000 at 05:36:28...
i: 21710000 at 05:36:30...
i: 21720000 at 05:36:32...
i: 21730000 at 05:36:33...
i: 21740000 at 05:36:35...
i: 21750000 at 05:36:37...
i: 21760000 at 05:36:39...
i: 21770000 at 05:36:40...
i: 21780000 at 05:36:42...
i: 21790000 at 05:36:44...
i: 21800000 at 05:36:45...
i: 21810000 at 05:36:47...
i: 21820000 at 05:36:49...
i: 21830000 at 05:36:50...
i: 21840000 at 05:36:52...
i: 21850000 at 05:36:54...
i: 21860000 at 05:36:56...
i: 21870000 at 05:36:57...
i: 21880000 at 05:36:59...
i: 21890000 at 05:37:01...
i: 21900000 at 05:37:02...
i: 21910000 at 05:37:04...
i: 21920000 at 05:37:06...
i: 21930000 at 05:37:07...
i: 21940000 at 05:37:09...
i: 21950000 at 05:37:11...
i: 21960000 at 05:37:13...
i: 21970000 at 05:37:14...
i: 21980000 at 05:37:16...
i: 21990000 at 05:37:18...
i: 22000000 at 05:37:19...
i: 22010000 at 05:37:21...
i: 22020000 at 05:37:23...
i: 22030000 at 05:37:25...
i: 22040000 at 05:37:26...
i

In [32]:
scaled2020_fb_band = create_tif_band(scaled2020_flat_df, "prophet")
print(scaled2020_fb_band.shape)

Start creating tif band at 05:38:32...
i: 0 at 05:38:32...
i: 10000 at 05:38:34...
i: 20000 at 05:38:35...
i: 30000 at 05:38:37...
i: 40000 at 05:38:39...
i: 50000 at 05:38:40...
i: 60000 at 05:38:42...
i: 70000 at 05:38:44...
i: 80000 at 05:38:46...
i: 90000 at 05:38:48...
i: 100000 at 05:38:49...
i: 110000 at 05:38:51...
i: 120000 at 05:38:53...
i: 130000 at 05:38:54...
i: 140000 at 05:38:56...
i: 150000 at 05:38:58...
i: 160000 at 05:39:00...
i: 170000 at 05:39:01...
i: 180000 at 05:39:03...
i: 190000 at 05:39:05...
i: 200000 at 05:39:07...
i: 210000 at 05:39:08...
i: 220000 at 05:39:10...
i: 230000 at 05:39:12...
i: 240000 at 05:39:13...
i: 250000 at 05:39:15...
i: 260000 at 05:39:17...
i: 270000 at 05:39:19...
i: 280000 at 05:39:21...
i: 290000 at 05:39:22...
i: 300000 at 05:39:24...
i: 310000 at 05:39:26...
i: 320000 at 05:39:28...
i: 330000 at 05:39:29...
i: 340000 at 05:39:31...
i: 350000 at 05:39:33...
i: 360000 at 05:39:34...
i: 370000 at 05:39:36...
i: 380000 at 05:39:38...


i: 3180000 at 05:47:43...
i: 3190000 at 05:47:44...
i: 3200000 at 05:47:46...
i: 3210000 at 05:47:48...
i: 3220000 at 05:47:50...
i: 3230000 at 05:47:51...
i: 3240000 at 05:47:53...
i: 3250000 at 05:47:55...
i: 3260000 at 05:47:56...
i: 3270000 at 05:47:58...
i: 3280000 at 05:48:00...
i: 3290000 at 05:48:02...
i: 3300000 at 05:48:03...
i: 3310000 at 05:48:05...
i: 3320000 at 05:48:07...
i: 3330000 at 05:48:09...
i: 3340000 at 05:48:10...
i: 3350000 at 05:48:12...
i: 3360000 at 05:48:14...
i: 3370000 at 05:48:16...
i: 3380000 at 05:48:17...
i: 3390000 at 05:48:19...
i: 3400000 at 05:48:21...
i: 3410000 at 05:48:22...
i: 3420000 at 05:48:24...
i: 3430000 at 05:48:26...
i: 3440000 at 05:48:28...
i: 3450000 at 05:48:29...
i: 3460000 at 05:48:31...
i: 3470000 at 05:48:33...
i: 3480000 at 05:48:34...
i: 3490000 at 05:48:36...
i: 3500000 at 05:48:38...
i: 3510000 at 05:48:40...
i: 3520000 at 05:48:41...
i: 3530000 at 05:48:43...
i: 3540000 at 05:48:45...
i: 3550000 at 05:48:46...
i: 3560000 a

i: 6340000 at 05:56:56...
i: 6350000 at 05:56:57...
i: 6360000 at 05:56:59...
i: 6370000 at 05:57:01...
i: 6380000 at 05:57:03...
i: 6390000 at 05:57:04...
i: 6400000 at 05:57:06...
i: 6410000 at 05:57:08...
i: 6420000 at 05:57:10...
i: 6430000 at 05:57:11...
i: 6440000 at 05:57:13...
i: 6450000 at 05:57:15...
i: 6460000 at 05:57:17...
i: 6470000 at 05:57:18...
i: 6480000 at 05:57:20...
i: 6490000 at 05:57:22...
i: 6500000 at 05:57:24...
i: 6510000 at 05:57:25...
i: 6520000 at 05:57:27...
i: 6530000 at 05:57:29...
i: 6540000 at 05:57:30...
i: 6550000 at 05:57:32...
i: 6560000 at 05:57:34...
i: 6570000 at 05:57:36...
i: 6580000 at 05:57:37...
i: 6590000 at 05:57:39...
i: 6600000 at 05:57:41...
i: 6610000 at 05:57:43...
i: 6620000 at 05:57:44...
i: 6630000 at 05:57:46...
i: 6640000 at 05:57:48...
i: 6650000 at 05:57:49...
i: 6660000 at 05:57:51...
i: 6670000 at 05:57:53...
i: 6680000 at 05:57:55...
i: 6690000 at 05:57:56...
i: 6700000 at 05:57:58...
i: 6710000 at 05:58:00...
i: 6720000 a

i: 9500000 at 06:06:02...
i: 9510000 at 06:06:04...
i: 9520000 at 06:06:06...
i: 9530000 at 06:06:08...
i: 9540000 at 06:06:09...
i: 9550000 at 06:06:11...
i: 9560000 at 06:06:13...
i: 9570000 at 06:06:15...
i: 9580000 at 06:06:16...
i: 9590000 at 06:06:18...
i: 9600000 at 06:06:20...
i: 9610000 at 06:06:21...
i: 9620000 at 06:06:23...
i: 9630000 at 06:06:25...
i: 9640000 at 06:06:27...
i: 9650000 at 06:06:28...
i: 9660000 at 06:06:30...
i: 9670000 at 06:06:32...
i: 9680000 at 06:06:33...
i: 9690000 at 06:06:35...
i: 9700000 at 06:06:37...
i: 9710000 at 06:06:39...
i: 9720000 at 06:06:40...
i: 9730000 at 06:06:42...
i: 9740000 at 06:06:44...
i: 9750000 at 06:06:45...
i: 9760000 at 06:06:47...
i: 9770000 at 06:06:49...
i: 9780000 at 06:06:51...
i: 9790000 at 06:06:52...
i: 9800000 at 06:06:54...
i: 9810000 at 06:06:56...
i: 9820000 at 06:06:58...
i: 9830000 at 06:06:59...
i: 9840000 at 06:07:01...
i: 9850000 at 06:07:03...
i: 9860000 at 06:07:04...
i: 9870000 at 06:07:06...
i: 9880000 a

i: 12560000 at 06:14:52...
i: 12570000 at 06:14:54...
i: 12580000 at 06:14:55...
i: 12590000 at 06:14:57...
i: 12600000 at 06:14:59...
i: 12610000 at 06:15:01...
i: 12620000 at 06:15:02...
i: 12630000 at 06:15:04...
i: 12640000 at 06:15:06...
i: 12650000 at 06:15:07...
i: 12660000 at 06:15:09...
i: 12670000 at 06:15:11...
i: 12680000 at 06:15:13...
i: 12690000 at 06:15:15...
i: 12700000 at 06:15:17...
i: 12710000 at 06:15:18...
i: 12720000 at 06:15:20...
i: 12730000 at 06:15:22...
i: 12740000 at 06:15:24...
i: 12750000 at 06:15:25...
i: 12760000 at 06:15:27...
i: 12770000 at 06:15:29...
i: 12780000 at 06:15:31...
i: 12790000 at 06:15:32...
i: 12800000 at 06:15:34...
i: 12810000 at 06:15:36...
i: 12820000 at 06:15:37...
i: 12830000 at 06:15:39...
i: 12840000 at 06:15:41...
i: 12850000 at 06:15:43...
i: 12860000 at 06:15:44...
i: 12870000 at 06:15:46...
i: 12880000 at 06:15:48...
i: 12890000 at 06:15:50...
i: 12900000 at 06:15:51...
i: 12910000 at 06:15:53...
i: 12920000 at 06:15:55...
i

i: 15600000 at 06:23:38...
i: 15610000 at 06:23:40...
i: 15620000 at 06:23:42...
i: 15630000 at 06:23:43...
i: 15640000 at 06:23:45...
i: 15650000 at 06:23:47...
i: 15660000 at 06:23:49...
i: 15670000 at 06:23:50...
i: 15680000 at 06:23:52...
i: 15690000 at 06:23:54...
i: 15700000 at 06:23:55...
i: 15710000 at 06:23:57...
i: 15720000 at 06:23:59...
i: 15730000 at 06:24:01...
i: 15740000 at 06:24:02...
i: 15750000 at 06:24:04...
i: 15760000 at 06:24:06...
i: 15770000 at 06:24:07...
i: 15780000 at 06:24:09...
i: 15790000 at 06:24:11...
i: 15800000 at 06:24:13...
i: 15810000 at 06:24:14...
i: 15820000 at 06:24:16...
i: 15830000 at 06:24:18...
i: 15840000 at 06:24:20...
i: 15850000 at 06:24:21...
i: 15860000 at 06:24:23...
i: 15870000 at 06:24:25...
i: 15880000 at 06:24:27...
i: 15890000 at 06:24:28...
i: 15900000 at 06:24:30...
i: 15910000 at 06:24:32...
i: 15920000 at 06:24:33...
i: 15930000 at 06:24:35...
i: 15940000 at 06:24:37...
i: 15950000 at 06:24:39...
i: 15960000 at 06:24:40...
i

i: 18640000 at 06:32:24...
i: 18650000 at 06:32:26...
i: 18660000 at 06:32:28...
i: 18670000 at 06:32:29...
i: 18680000 at 06:32:31...
i: 18690000 at 06:32:33...
i: 18700000 at 06:32:35...
i: 18710000 at 06:32:36...
i: 18720000 at 06:32:38...
i: 18730000 at 06:32:40...
i: 18740000 at 06:32:41...
i: 18750000 at 06:32:43...
i: 18760000 at 06:32:45...
i: 18770000 at 06:32:47...
i: 18780000 at 06:32:48...
i: 18790000 at 06:32:50...
i: 18800000 at 06:32:52...
i: 18810000 at 06:32:54...
i: 18820000 at 06:32:55...
i: 18830000 at 06:32:57...
i: 18840000 at 06:32:59...
i: 18850000 at 06:33:01...
i: 18860000 at 06:33:02...
i: 18870000 at 06:33:04...
i: 18880000 at 06:33:06...
i: 18890000 at 06:33:07...
i: 18900000 at 06:33:09...
i: 18910000 at 06:33:11...
i: 18920000 at 06:33:13...
i: 18930000 at 06:33:15...
i: 18940000 at 06:33:16...
i: 18950000 at 06:33:18...
i: 18960000 at 06:33:20...
i: 18970000 at 06:33:21...
i: 18980000 at 06:33:23...
i: 18990000 at 06:33:25...
i: 19000000 at 06:33:27...
i

i: 21680000 at 06:41:14...
i: 21690000 at 06:41:16...
i: 21700000 at 06:41:18...
i: 21710000 at 06:41:20...
i: 21720000 at 06:41:21...
i: 21730000 at 06:41:23...
i: 21740000 at 06:41:25...
i: 21750000 at 06:41:26...
i: 21760000 at 06:41:28...
i: 21770000 at 06:41:30...
i: 21780000 at 06:41:32...
i: 21790000 at 06:41:33...
i: 21800000 at 06:41:35...
i: 21810000 at 06:41:37...
i: 21820000 at 06:41:39...
i: 21830000 at 06:41:40...
i: 21840000 at 06:41:42...
i: 21850000 at 06:41:44...
i: 21860000 at 06:41:46...
i: 21870000 at 06:41:47...
i: 21880000 at 06:41:49...
i: 21890000 at 06:41:51...
i: 21900000 at 06:41:52...
i: 21910000 at 06:41:54...
i: 21920000 at 06:41:56...
i: 21930000 at 06:41:58...
i: 21940000 at 06:41:59...
i: 21950000 at 06:42:01...
i: 21960000 at 06:42:03...
i: 21970000 at 06:42:05...
i: 21980000 at 06:42:06...
i: 21990000 at 06:42:08...
i: 22000000 at 06:42:10...
i: 22010000 at 06:42:11...
i: 22020000 at 06:42:13...
i: 22030000 at 06:42:15...
i: 22040000 at 06:42:17...
i

In [33]:
scaled2020_fbe_band = create_tif_band(scaled2020_flat_df, "prophet_rmse")
print(scaled2020_fbe_band.shape)

Start creating tif band at 06:43:23...
i: 0 at 06:43:23...
i: 10000 at 06:43:25...
i: 20000 at 06:43:27...
i: 30000 at 06:43:29...
i: 40000 at 06:43:30...
i: 50000 at 06:43:32...
i: 60000 at 06:43:34...
i: 70000 at 06:43:36...
i: 80000 at 06:43:37...
i: 90000 at 06:43:39...
i: 100000 at 06:43:41...
i: 110000 at 06:43:42...
i: 120000 at 06:43:44...
i: 130000 at 06:43:46...
i: 140000 at 06:43:48...
i: 150000 at 06:43:49...
i: 160000 at 06:43:51...
i: 170000 at 06:43:53...
i: 180000 at 06:43:55...
i: 190000 at 06:43:56...
i: 200000 at 06:43:58...
i: 210000 at 06:44:00...
i: 220000 at 06:44:01...
i: 230000 at 06:44:03...
i: 240000 at 06:44:05...
i: 250000 at 06:44:07...
i: 260000 at 06:44:08...
i: 270000 at 06:44:10...
i: 280000 at 06:44:12...
i: 290000 at 06:44:14...
i: 300000 at 06:44:15...
i: 310000 at 06:44:17...
i: 320000 at 06:44:19...
i: 330000 at 06:44:21...
i: 340000 at 06:44:22...
i: 350000 at 06:44:24...
i: 360000 at 06:44:26...
i: 370000 at 06:44:27...
i: 380000 at 06:44:29...


i: 3180000 at 06:52:35...
i: 3190000 at 06:52:36...
i: 3200000 at 06:52:38...
i: 3210000 at 06:52:40...
i: 3220000 at 06:52:41...
i: 3230000 at 06:52:43...
i: 3240000 at 06:52:45...
i: 3250000 at 06:52:47...
i: 3260000 at 06:52:48...
i: 3270000 at 06:52:50...
i: 3280000 at 06:52:52...
i: 3290000 at 06:52:53...
i: 3300000 at 06:52:55...
i: 3310000 at 06:52:57...
i: 3320000 at 06:52:59...
i: 3330000 at 06:53:00...
i: 3340000 at 06:53:02...
i: 3350000 at 06:53:04...
i: 3360000 at 06:53:06...
i: 3370000 at 06:53:07...
i: 3380000 at 06:53:09...
i: 3390000 at 06:53:11...
i: 3400000 at 06:53:12...
i: 3410000 at 06:53:14...
i: 3420000 at 06:53:16...
i: 3430000 at 06:53:18...
i: 3440000 at 06:53:19...
i: 3450000 at 06:53:21...
i: 3460000 at 06:53:23...
i: 3470000 at 06:53:25...
i: 3480000 at 06:53:26...
i: 3490000 at 06:53:28...
i: 3500000 at 06:53:30...
i: 3510000 at 06:53:32...
i: 3520000 at 06:53:33...
i: 3530000 at 06:53:35...
i: 3540000 at 06:53:37...
i: 3550000 at 06:53:39...
i: 3560000 a

i: 6340000 at 07:01:42...
i: 6350000 at 07:01:44...
i: 6360000 at 07:01:45...
i: 6370000 at 07:01:47...
i: 6380000 at 07:01:49...
i: 6390000 at 07:01:51...
i: 6400000 at 07:01:52...
i: 6410000 at 07:01:54...
i: 6420000 at 07:01:56...
i: 6430000 at 07:01:58...
i: 6440000 at 07:01:59...
i: 6450000 at 07:02:01...
i: 6460000 at 07:02:03...
i: 6470000 at 07:02:04...
i: 6480000 at 07:02:06...
i: 6490000 at 07:02:08...
i: 6500000 at 07:02:10...
i: 6510000 at 07:02:11...
i: 6520000 at 07:02:13...
i: 6530000 at 07:02:15...
i: 6540000 at 07:02:17...
i: 6550000 at 07:02:18...
i: 6560000 at 07:02:20...
i: 6570000 at 07:02:22...
i: 6580000 at 07:02:23...
i: 6590000 at 07:02:25...
i: 6600000 at 07:02:27...
i: 6610000 at 07:02:29...
i: 6620000 at 07:02:30...
i: 6630000 at 07:02:32...
i: 6640000 at 07:02:34...
i: 6650000 at 07:02:36...
i: 6660000 at 07:02:37...
i: 6670000 at 07:02:39...
i: 6680000 at 07:02:41...
i: 6690000 at 07:02:42...
i: 6700000 at 07:02:44...
i: 6710000 at 07:02:46...
i: 6720000 a

i: 9500000 at 07:10:51...
i: 9510000 at 07:10:52...
i: 9520000 at 07:10:54...
i: 9530000 at 07:10:56...
i: 9540000 at 07:10:58...
i: 9550000 at 07:10:59...
i: 9560000 at 07:11:01...
i: 9570000 at 07:11:03...
i: 9580000 at 07:11:05...
i: 9590000 at 07:11:06...
i: 9600000 at 07:11:08...
i: 9610000 at 07:11:10...
i: 9620000 at 07:11:12...
i: 9630000 at 07:11:13...
i: 9640000 at 07:11:15...
i: 9650000 at 07:11:17...
i: 9660000 at 07:11:19...
i: 9670000 at 07:11:20...
i: 9680000 at 07:11:22...
i: 9690000 at 07:11:24...
i: 9700000 at 07:11:26...
i: 9710000 at 07:11:27...
i: 9720000 at 07:11:29...
i: 9730000 at 07:11:31...
i: 9740000 at 07:11:32...
i: 9750000 at 07:11:34...
i: 9760000 at 07:11:36...
i: 9770000 at 07:11:38...
i: 9780000 at 07:11:39...
i: 9790000 at 07:11:41...
i: 9800000 at 07:11:43...
i: 9810000 at 07:11:45...
i: 9820000 at 07:11:46...
i: 9830000 at 07:11:48...
i: 9840000 at 07:11:50...
i: 9850000 at 07:11:51...
i: 9860000 at 07:11:53...
i: 9870000 at 07:11:55...
i: 9880000 a

i: 12560000 at 07:19:41...
i: 12570000 at 07:19:42...
i: 12580000 at 07:19:44...
i: 12590000 at 07:19:46...
i: 12600000 at 07:19:48...
i: 12610000 at 07:19:49...
i: 12620000 at 07:19:51...
i: 12630000 at 07:19:53...
i: 12640000 at 07:19:54...
i: 12650000 at 07:19:56...
i: 12660000 at 07:19:58...
i: 12670000 at 07:20:00...
i: 12680000 at 07:20:01...
i: 12690000 at 07:20:03...
i: 12700000 at 07:20:05...
i: 12710000 at 07:20:07...
i: 12720000 at 07:20:08...
i: 12730000 at 07:20:10...
i: 12740000 at 07:20:12...
i: 12750000 at 07:20:14...
i: 12760000 at 07:20:15...
i: 12770000 at 07:20:17...
i: 12780000 at 07:20:19...
i: 12790000 at 07:20:21...
i: 12800000 at 07:20:22...
i: 12810000 at 07:20:24...
i: 12820000 at 07:20:26...
i: 12830000 at 07:20:28...
i: 12840000 at 07:20:29...
i: 12850000 at 07:20:31...
i: 12860000 at 07:20:33...
i: 12870000 at 07:20:35...
i: 12880000 at 07:20:36...
i: 12890000 at 07:20:38...
i: 12900000 at 07:20:40...
i: 12910000 at 07:20:41...
i: 12920000 at 07:20:43...
i

i: 15600000 at 07:28:27...
i: 15610000 at 07:28:29...
i: 15620000 at 07:28:30...
i: 15630000 at 07:28:32...
i: 15640000 at 07:28:34...
i: 15650000 at 07:28:36...
i: 15660000 at 07:28:37...
i: 15670000 at 07:28:39...
i: 15680000 at 07:28:41...
i: 15690000 at 07:28:43...
i: 15700000 at 07:28:44...
i: 15710000 at 07:28:46...
i: 15720000 at 07:28:48...
i: 15730000 at 07:28:49...
i: 15740000 at 07:28:51...
i: 15750000 at 07:28:53...
i: 15760000 at 07:28:55...
i: 15770000 at 07:28:56...
i: 15780000 at 07:28:58...
i: 15790000 at 07:29:00...
i: 15800000 at 07:29:01...
i: 15810000 at 07:29:03...
i: 15820000 at 07:29:05...
i: 15830000 at 07:29:07...
i: 15840000 at 07:29:08...
i: 15850000 at 07:29:10...
i: 15860000 at 07:29:12...
i: 15870000 at 07:29:14...
i: 15880000 at 07:29:15...
i: 15890000 at 07:29:17...
i: 15900000 at 07:29:19...
i: 15910000 at 07:29:21...
i: 15920000 at 07:29:22...
i: 15930000 at 07:29:24...
i: 15940000 at 07:29:26...
i: 15950000 at 07:29:28...
i: 15960000 at 07:29:29...
i

i: 18640000 at 07:37:13...
i: 18650000 at 07:37:15...
i: 18660000 at 07:37:17...
i: 18670000 at 07:37:19...
i: 18680000 at 07:37:20...
i: 18690000 at 07:37:22...
i: 18700000 at 07:37:24...
i: 18710000 at 07:37:26...
i: 18720000 at 07:37:27...
i: 18730000 at 07:37:29...
i: 18740000 at 07:37:31...
i: 18750000 at 07:37:32...
i: 18760000 at 07:37:34...
i: 18770000 at 07:37:36...
i: 18780000 at 07:37:38...
i: 18790000 at 07:37:39...
i: 18800000 at 07:37:41...
i: 18810000 at 07:37:43...
i: 18820000 at 07:37:44...
i: 18830000 at 07:37:46...
i: 18840000 at 07:37:48...
i: 18850000 at 07:37:50...
i: 18860000 at 07:37:51...
i: 18870000 at 07:37:53...
i: 18880000 at 07:37:55...
i: 18890000 at 07:37:57...
i: 18900000 at 07:37:58...
i: 18910000 at 07:38:00...
i: 18920000 at 07:38:02...
i: 18930000 at 07:38:03...
i: 18940000 at 07:38:05...
i: 18950000 at 07:38:07...
i: 18960000 at 07:38:09...
i: 18970000 at 07:38:10...
i: 18980000 at 07:38:12...
i: 18990000 at 07:38:14...
i: 19000000 at 07:38:16...
i

i: 21680000 at 07:46:00...
i: 21690000 at 07:46:01...
i: 21700000 at 07:46:03...
i: 21710000 at 07:46:05...
i: 21720000 at 07:46:07...
i: 21730000 at 07:46:08...
i: 21740000 at 07:46:10...
i: 21750000 at 07:46:12...
i: 21760000 at 07:46:13...
i: 21770000 at 07:46:15...
i: 21780000 at 07:46:17...
i: 21790000 at 07:46:19...
i: 21800000 at 07:46:20...
i: 21810000 at 07:46:22...
i: 21820000 at 07:46:24...
i: 21830000 at 07:46:26...
i: 21840000 at 07:46:27...
i: 21850000 at 07:46:29...
i: 21860000 at 07:46:31...
i: 21870000 at 07:46:32...
i: 21880000 at 07:46:34...
i: 21890000 at 07:46:36...
i: 21900000 at 07:46:38...
i: 21910000 at 07:46:39...
i: 21920000 at 07:46:41...
i: 21930000 at 07:46:43...
i: 21940000 at 07:46:45...
i: 21950000 at 07:46:46...
i: 21960000 at 07:46:48...
i: 21970000 at 07:46:50...
i: 21980000 at 07:46:51...
i: 21990000 at 07:46:53...
i: 22000000 at 07:46:55...
i: 22010000 at 07:46:57...
i: 22020000 at 07:46:58...
i: 22030000 at 07:47:00...
i: 22040000 at 07:47:02...
i

In [34]:
scaled2020_th_band = create_tif_band(scaled2020_flat_df, "lstm_tanh")
print(scaled2020_th_band.shape)

Start creating tif band at 07:48:08...
i: 0 at 07:48:09...
i: 10000 at 07:48:11...
i: 20000 at 07:48:12...
i: 30000 at 07:48:14...
i: 40000 at 07:48:16...
i: 50000 at 07:48:18...
i: 60000 at 07:48:19...
i: 70000 at 07:48:21...
i: 80000 at 07:48:23...
i: 90000 at 07:48:24...
i: 100000 at 07:48:26...
i: 110000 at 07:48:28...
i: 120000 at 07:48:30...
i: 130000 at 07:48:31...
i: 140000 at 07:48:33...
i: 150000 at 07:48:35...
i: 160000 at 07:48:37...
i: 170000 at 07:48:38...
i: 180000 at 07:48:40...
i: 190000 at 07:48:42...
i: 200000 at 07:48:44...
i: 210000 at 07:48:45...
i: 220000 at 07:48:47...
i: 230000 at 07:48:49...
i: 240000 at 07:48:50...
i: 250000 at 07:48:52...
i: 260000 at 07:48:54...
i: 270000 at 07:48:56...
i: 280000 at 07:48:57...
i: 290000 at 07:48:59...
i: 300000 at 07:49:01...
i: 310000 at 07:49:03...
i: 320000 at 07:49:04...
i: 330000 at 07:49:06...
i: 340000 at 07:49:08...
i: 350000 at 07:49:10...
i: 360000 at 07:49:11...
i: 370000 at 07:49:13...
i: 380000 at 07:49:15...


i: 3180000 at 07:57:22...
i: 3190000 at 07:57:24...
i: 3200000 at 07:57:26...
i: 3210000 at 07:57:27...
i: 3220000 at 07:57:29...
i: 3230000 at 07:57:31...
i: 3240000 at 07:57:33...
i: 3250000 at 07:57:34...
i: 3260000 at 07:57:36...
i: 3270000 at 07:57:38...
i: 3280000 at 07:57:39...
i: 3290000 at 07:57:41...
i: 3300000 at 07:57:43...
i: 3310000 at 07:57:45...
i: 3320000 at 07:57:47...
i: 3330000 at 07:57:48...
i: 3340000 at 07:57:50...
i: 3350000 at 07:57:52...
i: 3360000 at 07:57:54...
i: 3370000 at 07:57:55...
i: 3380000 at 07:57:57...
i: 3390000 at 07:57:59...
i: 3400000 at 07:58:00...
i: 3410000 at 07:58:02...
i: 3420000 at 07:58:04...
i: 3430000 at 07:58:06...
i: 3440000 at 07:58:07...
i: 3450000 at 07:58:09...
i: 3460000 at 07:58:11...
i: 3470000 at 07:58:13...
i: 3480000 at 07:58:14...
i: 3490000 at 07:58:16...
i: 3500000 at 07:58:18...
i: 3510000 at 07:58:20...
i: 3520000 at 07:58:21...
i: 3530000 at 07:58:23...
i: 3540000 at 07:58:25...
i: 3550000 at 07:58:26...
i: 3560000 a

i: 6340000 at 08:06:32...
i: 6350000 at 08:06:34...
i: 6360000 at 08:06:36...
i: 6370000 at 08:06:37...
i: 6380000 at 08:06:39...
i: 6390000 at 08:06:41...
i: 6400000 at 08:06:43...
i: 6410000 at 08:06:44...
i: 6420000 at 08:06:46...
i: 6430000 at 08:06:48...
i: 6440000 at 08:06:50...
i: 6450000 at 08:06:51...
i: 6460000 at 08:06:53...
i: 6470000 at 08:06:55...
i: 6480000 at 08:06:56...
i: 6490000 at 08:06:58...
i: 6500000 at 08:07:00...
i: 6510000 at 08:07:02...
i: 6520000 at 08:07:03...
i: 6530000 at 08:07:05...
i: 6540000 at 08:07:07...
i: 6550000 at 08:07:09...
i: 6560000 at 08:07:10...
i: 6570000 at 08:07:12...
i: 6580000 at 08:07:14...
i: 6590000 at 08:07:16...
i: 6600000 at 08:07:17...
i: 6610000 at 08:07:19...
i: 6620000 at 08:07:21...
i: 6630000 at 08:07:23...
i: 6640000 at 08:07:24...
i: 6650000 at 08:07:26...
i: 6660000 at 08:07:28...
i: 6670000 at 08:07:30...
i: 6680000 at 08:07:31...
i: 6690000 at 08:07:33...
i: 6700000 at 08:07:35...
i: 6710000 at 08:07:37...
i: 6720000 a

i: 9500000 at 08:15:42...
i: 9510000 at 08:15:44...
i: 9520000 at 08:15:46...
i: 9530000 at 08:15:48...
i: 9540000 at 08:15:49...
i: 9550000 at 08:15:51...
i: 9560000 at 08:15:53...
i: 9570000 at 08:15:55...
i: 9580000 at 08:15:56...
i: 9590000 at 08:15:58...
i: 9600000 at 08:16:00...
i: 9610000 at 08:16:02...
i: 9620000 at 08:16:03...
i: 9630000 at 08:16:05...
i: 9640000 at 08:16:07...
i: 9650000 at 08:16:09...
i: 9660000 at 08:16:10...
i: 9670000 at 08:16:12...
i: 9680000 at 08:16:14...
i: 9690000 at 08:16:16...
i: 9700000 at 08:16:17...
i: 9710000 at 08:16:19...
i: 9720000 at 08:16:21...
i: 9730000 at 08:16:22...
i: 9740000 at 08:16:24...
i: 9750000 at 08:16:26...
i: 9760000 at 08:16:28...
i: 9770000 at 08:16:29...
i: 9780000 at 08:16:31...
i: 9790000 at 08:16:33...
i: 9800000 at 08:16:35...
i: 9810000 at 08:16:36...
i: 9820000 at 08:16:38...
i: 9830000 at 08:16:40...
i: 9840000 at 08:16:41...
i: 9850000 at 08:16:43...
i: 9860000 at 08:16:45...
i: 9870000 at 08:16:47...
i: 9880000 a

i: 12560000 at 08:24:35...
i: 12570000 at 08:24:36...
i: 12580000 at 08:24:38...
i: 12590000 at 08:24:40...
i: 12600000 at 08:24:42...
i: 12610000 at 08:24:44...
i: 12620000 at 08:24:45...
i: 12630000 at 08:24:47...
i: 12640000 at 08:24:49...
i: 12650000 at 08:24:50...
i: 12660000 at 08:24:52...
i: 12670000 at 08:24:54...
i: 12680000 at 08:24:56...
i: 12690000 at 08:24:57...
i: 12700000 at 08:24:59...
i: 12710000 at 08:25:01...
i: 12720000 at 08:25:03...
i: 12730000 at 08:25:04...
i: 12740000 at 08:25:06...
i: 12750000 at 08:25:08...
i: 12760000 at 08:25:10...
i: 12770000 at 08:25:12...
i: 12780000 at 08:25:13...
i: 12790000 at 08:25:15...
i: 12800000 at 08:25:17...
i: 12810000 at 08:25:19...
i: 12820000 at 08:25:20...
i: 12830000 at 08:25:22...
i: 12840000 at 08:25:24...
i: 12850000 at 08:25:26...
i: 12860000 at 08:25:27...
i: 12870000 at 08:25:29...
i: 12880000 at 08:25:31...
i: 12890000 at 08:25:33...
i: 12900000 at 08:25:34...
i: 12910000 at 08:25:36...
i: 12920000 at 08:25:38...
i

i: 15600000 at 08:33:25...
i: 15610000 at 08:33:27...
i: 15620000 at 08:33:28...
i: 15630000 at 08:33:30...
i: 15640000 at 08:33:32...
i: 15650000 at 08:33:34...
i: 15660000 at 08:33:35...
i: 15670000 at 08:33:37...
i: 15680000 at 08:33:39...
i: 15690000 at 08:33:40...
i: 15700000 at 08:33:42...
i: 15710000 at 08:33:44...
i: 15720000 at 08:33:46...
i: 15730000 at 08:33:47...
i: 15740000 at 08:33:49...
i: 15750000 at 08:33:51...
i: 15760000 at 08:33:53...
i: 15770000 at 08:33:54...
i: 15780000 at 08:33:56...
i: 15790000 at 08:33:58...
i: 15800000 at 08:33:59...
i: 15810000 at 08:34:01...
i: 15820000 at 08:34:03...
i: 15830000 at 08:34:05...
i: 15840000 at 08:34:06...
i: 15850000 at 08:34:08...
i: 15860000 at 08:34:10...
i: 15870000 at 08:34:12...
i: 15880000 at 08:34:13...
i: 15890000 at 08:34:15...
i: 15900000 at 08:34:17...
i: 15910000 at 08:34:19...
i: 15920000 at 08:34:20...
i: 15930000 at 08:34:22...
i: 15940000 at 08:34:24...
i: 15950000 at 08:34:26...
i: 15960000 at 08:34:27...
i

i: 18640000 at 08:42:15...
i: 18650000 at 08:42:17...
i: 18660000 at 08:42:18...
i: 18670000 at 08:42:20...
i: 18680000 at 08:42:22...
i: 18690000 at 08:42:23...
i: 18700000 at 08:42:25...
i: 18710000 at 08:42:27...
i: 18720000 at 08:42:29...
i: 18730000 at 08:42:30...
i: 18740000 at 08:42:32...
i: 18750000 at 08:42:34...
i: 18760000 at 08:42:36...
i: 18770000 at 08:42:37...
i: 18780000 at 08:42:39...
i: 18790000 at 08:42:41...
i: 18800000 at 08:42:43...
i: 18810000 at 08:42:44...
i: 18820000 at 08:42:46...
i: 18830000 at 08:42:48...
i: 18840000 at 08:42:50...
i: 18850000 at 08:42:51...
i: 18860000 at 08:42:53...
i: 18870000 at 08:42:55...
i: 18880000 at 08:42:56...
i: 18890000 at 08:42:58...
i: 18900000 at 08:43:00...
i: 18910000 at 08:43:02...
i: 18920000 at 08:43:03...
i: 18930000 at 08:43:05...
i: 18940000 at 08:43:07...
i: 18950000 at 08:43:09...
i: 18960000 at 08:43:10...
i: 18970000 at 08:43:12...
i: 18980000 at 08:43:14...
i: 18990000 at 08:43:16...
i: 19000000 at 08:43:17...
i

i: 21680000 at 08:51:03...
i: 21690000 at 08:51:05...
i: 21700000 at 08:51:07...
i: 21710000 at 08:51:09...
i: 21720000 at 08:51:10...
i: 21730000 at 08:51:12...
i: 21740000 at 08:51:14...
i: 21750000 at 08:51:16...
i: 21760000 at 08:51:18...
i: 21770000 at 08:51:19...
i: 21780000 at 08:51:21...
i: 21790000 at 08:51:23...
i: 21800000 at 08:51:25...
i: 21810000 at 08:51:26...
i: 21820000 at 08:51:28...
i: 21830000 at 08:51:30...
i: 21840000 at 08:51:31...
i: 21850000 at 08:51:33...
i: 21860000 at 08:51:35...
i: 21870000 at 08:51:37...
i: 21880000 at 08:51:38...
i: 21890000 at 08:51:40...
i: 21900000 at 08:51:42...
i: 21910000 at 08:51:44...
i: 21920000 at 08:51:45...
i: 21930000 at 08:51:47...
i: 21940000 at 08:51:49...
i: 21950000 at 08:51:51...
i: 21960000 at 08:51:52...
i: 21970000 at 08:51:54...
i: 21980000 at 08:51:56...
i: 21990000 at 08:51:57...
i: 22000000 at 08:51:59...
i: 22010000 at 08:52:01...
i: 22020000 at 08:52:03...
i: 22030000 at 08:52:04...
i: 22040000 at 08:52:06...
i

In [35]:
scaled2020_the_band = create_tif_band(scaled2020_flat_df, "lstm_tanh_rmse")
print(scaled2020_the_band.shape)

Start creating tif band at 08:53:13...
i: 0 at 08:53:13...
i: 10000 at 08:53:15...
i: 20000 at 08:53:17...
i: 30000 at 08:53:19...
i: 40000 at 08:53:20...
i: 50000 at 08:53:22...
i: 60000 at 08:53:24...
i: 70000 at 08:53:26...
i: 80000 at 08:53:27...
i: 90000 at 08:53:29...
i: 100000 at 08:53:31...
i: 110000 at 08:53:33...
i: 120000 at 08:53:34...
i: 130000 at 08:53:36...
i: 140000 at 08:53:38...
i: 150000 at 08:53:40...
i: 160000 at 08:53:41...
i: 170000 at 08:53:43...
i: 180000 at 08:53:45...
i: 190000 at 08:53:46...
i: 200000 at 08:53:48...
i: 210000 at 08:53:50...
i: 220000 at 08:53:52...
i: 230000 at 08:53:53...
i: 240000 at 08:53:55...
i: 250000 at 08:53:57...
i: 260000 at 08:53:58...
i: 270000 at 08:54:00...
i: 280000 at 08:54:02...
i: 290000 at 08:54:04...
i: 300000 at 08:54:05...
i: 310000 at 08:54:07...
i: 320000 at 08:54:09...
i: 330000 at 08:54:10...
i: 340000 at 08:54:12...
i: 350000 at 08:54:14...
i: 360000 at 08:54:16...
i: 370000 at 08:54:17...
i: 380000 at 08:54:19...


i: 3180000 at 09:02:21...
i: 3190000 at 09:02:23...
i: 3200000 at 09:02:25...
i: 3210000 at 09:02:26...
i: 3220000 at 09:02:28...
i: 3230000 at 09:02:30...
i: 3240000 at 09:02:32...
i: 3250000 at 09:02:33...
i: 3260000 at 09:02:35...
i: 3270000 at 09:02:37...
i: 3280000 at 09:02:39...
i: 3290000 at 09:02:40...
i: 3300000 at 09:02:42...
i: 3310000 at 09:02:44...
i: 3320000 at 09:02:45...
i: 3330000 at 09:02:47...
i: 3340000 at 09:02:49...
i: 3350000 at 09:02:51...
i: 3360000 at 09:02:52...
i: 3370000 at 09:02:54...
i: 3380000 at 09:02:56...
i: 3390000 at 09:02:57...
i: 3400000 at 09:02:59...
i: 3410000 at 09:03:01...
i: 3420000 at 09:03:02...
i: 3430000 at 09:03:04...
i: 3440000 at 09:03:06...
i: 3450000 at 09:03:08...
i: 3460000 at 09:03:09...
i: 3470000 at 09:03:11...
i: 3480000 at 09:03:13...
i: 3490000 at 09:03:14...
i: 3500000 at 09:03:16...
i: 3510000 at 09:03:18...
i: 3520000 at 09:03:20...
i: 3530000 at 09:03:21...
i: 3540000 at 09:03:23...
i: 3550000 at 09:03:25...
i: 3560000 a

i: 6340000 at 09:11:25...
i: 6350000 at 09:11:27...
i: 6360000 at 09:11:28...
i: 6370000 at 09:11:30...
i: 6380000 at 09:11:32...
i: 6390000 at 09:11:33...
i: 6400000 at 09:11:35...
i: 6410000 at 09:11:37...
i: 6420000 at 09:11:39...
i: 6430000 at 09:11:40...
i: 6440000 at 09:11:42...
i: 6450000 at 09:11:44...
i: 6460000 at 09:11:46...
i: 6470000 at 09:11:47...
i: 6480000 at 09:11:49...
i: 6490000 at 09:11:51...
i: 6500000 at 09:11:53...
i: 6510000 at 09:11:54...
i: 6520000 at 09:11:56...
i: 6530000 at 09:11:58...
i: 6540000 at 09:11:59...
i: 6550000 at 09:12:01...
i: 6560000 at 09:12:03...
i: 6570000 at 09:12:05...
i: 6580000 at 09:12:06...
i: 6590000 at 09:12:08...
i: 6600000 at 09:12:10...
i: 6610000 at 09:12:11...
i: 6620000 at 09:12:13...
i: 6630000 at 09:12:15...
i: 6640000 at 09:12:17...
i: 6650000 at 09:12:18...
i: 6660000 at 09:12:20...
i: 6670000 at 09:12:22...
i: 6680000 at 09:12:24...
i: 6690000 at 09:12:25...
i: 6700000 at 09:12:27...
i: 6710000 at 09:12:29...
i: 6720000 a

i: 9500000 at 09:20:29...
i: 9510000 at 09:20:30...
i: 9520000 at 09:20:32...
i: 9530000 at 09:20:34...
i: 9540000 at 09:20:35...
i: 9550000 at 09:20:37...
i: 9560000 at 09:20:39...
i: 9570000 at 09:20:40...
i: 9580000 at 09:20:42...
i: 9590000 at 09:20:44...
i: 9600000 at 09:20:46...
i: 9610000 at 09:20:47...
i: 9620000 at 09:20:49...
i: 9630000 at 09:20:51...
i: 9640000 at 09:20:53...
i: 9650000 at 09:20:54...
i: 9660000 at 09:20:56...
i: 9670000 at 09:20:58...
i: 9680000 at 09:20:59...
i: 9690000 at 09:21:01...
i: 9700000 at 09:21:03...
i: 9710000 at 09:21:04...
i: 9720000 at 09:21:06...
i: 9730000 at 09:21:08...
i: 9740000 at 09:21:10...
i: 9750000 at 09:21:11...
i: 9760000 at 09:21:13...
i: 9770000 at 09:21:15...
i: 9780000 at 09:21:17...
i: 9790000 at 09:21:18...
i: 9800000 at 09:21:20...
i: 9810000 at 09:21:22...
i: 9820000 at 09:21:23...
i: 9830000 at 09:21:25...
i: 9840000 at 09:21:27...
i: 9850000 at 09:21:29...
i: 9860000 at 09:21:30...
i: 9870000 at 09:21:32...
i: 9880000 a

i: 12560000 at 09:29:14...
i: 12570000 at 09:29:16...
i: 12580000 at 09:29:18...
i: 12590000 at 09:29:20...
i: 12600000 at 09:29:21...
i: 12610000 at 09:29:23...
i: 12620000 at 09:29:25...
i: 12630000 at 09:29:27...
i: 12640000 at 09:29:28...
i: 12650000 at 09:29:30...
i: 12660000 at 09:29:32...
i: 12670000 at 09:29:33...
i: 12680000 at 09:29:35...
i: 12690000 at 09:29:37...
i: 12700000 at 09:29:39...
i: 12710000 at 09:29:40...
i: 12720000 at 09:29:42...
i: 12730000 at 09:29:44...
i: 12740000 at 09:29:45...
i: 12750000 at 09:29:47...
i: 12760000 at 09:29:49...
i: 12770000 at 09:29:51...
i: 12780000 at 09:29:52...
i: 12790000 at 09:29:54...
i: 12800000 at 09:29:56...
i: 12810000 at 09:29:57...
i: 12820000 at 09:29:59...
i: 12830000 at 09:30:01...
i: 12840000 at 09:30:03...
i: 12850000 at 09:30:05...
i: 12860000 at 09:30:07...
i: 12870000 at 09:30:09...
i: 12880000 at 09:30:10...
i: 12890000 at 09:30:12...
i: 12900000 at 09:30:14...
i: 12910000 at 09:30:16...
i: 12920000 at 09:30:17...
i

i: 15600000 at 09:37:57...
i: 15610000 at 09:37:59...
i: 15620000 at 09:38:01...
i: 15630000 at 09:38:03...
i: 15640000 at 09:38:04...
i: 15650000 at 09:38:06...
i: 15660000 at 09:38:08...
i: 15670000 at 09:38:09...
i: 15680000 at 09:38:11...
i: 15690000 at 09:38:13...
i: 15700000 at 09:38:15...
i: 15710000 at 09:38:16...
i: 15720000 at 09:38:18...
i: 15730000 at 09:38:20...
i: 15740000 at 09:38:21...
i: 15750000 at 09:38:23...
i: 15760000 at 09:38:25...
i: 15770000 at 09:38:27...
i: 15780000 at 09:38:28...
i: 15790000 at 09:38:30...
i: 15800000 at 09:38:32...
i: 15810000 at 09:38:33...
i: 15820000 at 09:38:35...
i: 15830000 at 09:38:37...
i: 15840000 at 09:38:39...
i: 15850000 at 09:38:40...
i: 15860000 at 09:38:42...
i: 15870000 at 09:38:44...
i: 15880000 at 09:38:45...
i: 15890000 at 09:38:47...
i: 15900000 at 09:38:49...
i: 15910000 at 09:38:51...
i: 15920000 at 09:38:52...
i: 15930000 at 09:38:54...
i: 15940000 at 09:38:56...
i: 15950000 at 09:38:57...
i: 15960000 at 09:38:59...
i

i: 18640000 at 09:46:40...
i: 18650000 at 09:46:42...
i: 18660000 at 09:46:44...
i: 18670000 at 09:46:45...
i: 18680000 at 09:46:47...
i: 18690000 at 09:46:49...
i: 18700000 at 09:46:51...
i: 18710000 at 09:46:52...
i: 18720000 at 09:46:54...
i: 18730000 at 09:46:56...
i: 18740000 at 09:46:57...
i: 18750000 at 09:46:59...
i: 18760000 at 09:47:01...
i: 18770000 at 09:47:03...
i: 18780000 at 09:47:04...
i: 18790000 at 09:47:06...
i: 18800000 at 09:47:08...
i: 18810000 at 09:47:09...
i: 18820000 at 09:47:11...
i: 18830000 at 09:47:13...
i: 18840000 at 09:47:15...
i: 18850000 at 09:47:16...
i: 18860000 at 09:47:18...
i: 18870000 at 09:47:20...
i: 18880000 at 09:47:22...
i: 18890000 at 09:47:23...
i: 18900000 at 09:47:25...
i: 18910000 at 09:47:27...
i: 18920000 at 09:47:29...
i: 18930000 at 09:47:30...
i: 18940000 at 09:47:32...
i: 18950000 at 09:47:34...
i: 18960000 at 09:47:35...
i: 18970000 at 09:47:37...
i: 18980000 at 09:47:39...
i: 18990000 at 09:47:41...
i: 19000000 at 09:47:42...
i

i: 21680000 at 09:55:24...
i: 21690000 at 09:55:26...
i: 21700000 at 09:55:27...
i: 21710000 at 09:55:29...
i: 21720000 at 09:55:31...
i: 21730000 at 09:55:33...
i: 21740000 at 09:55:34...
i: 21750000 at 09:55:36...
i: 21760000 at 09:55:38...
i: 21770000 at 09:55:39...
i: 21780000 at 09:55:41...
i: 21790000 at 09:55:43...
i: 21800000 at 09:55:45...
i: 21810000 at 09:55:46...
i: 21820000 at 09:55:48...
i: 21830000 at 09:55:50...
i: 21840000 at 09:55:51...
i: 21850000 at 09:55:53...
i: 21860000 at 09:55:55...
i: 21870000 at 09:55:57...
i: 21880000 at 09:55:58...
i: 21890000 at 09:56:00...
i: 21900000 at 09:56:02...
i: 21910000 at 09:56:03...
i: 21920000 at 09:56:05...
i: 21930000 at 09:56:07...
i: 21940000 at 09:56:09...
i: 21950000 at 09:56:10...
i: 21960000 at 09:56:12...
i: 21970000 at 09:56:14...
i: 21980000 at 09:56:16...
i: 21990000 at 09:56:17...
i: 22000000 at 09:56:19...
i: 22010000 at 09:56:21...
i: 22020000 at 09:56:22...
i: 22030000 at 09:56:24...
i: 22040000 at 09:56:26...
i

In [36]:
scaled0817_df = pd.read_pickle("results/scaled0817.pkl")
scaled0817_df

y     x       lat         lon  windvelo
0         5801     0  7.675769  116.041573       NaN
1         5802     0  7.673269  116.041573       NaN
2         5803     0  7.670769  116.041573       NaN
3         5804     0  7.668269  116.041573       NaN
4         5805     0  7.665769  116.041573       NaN
...        ...   ...       ...         ...       ...
22423447  5957  4950  7.285769  128.416580       NaN
22423448  5958  4950  7.283269  128.416580       NaN
22423449  5959  4950  7.280769  128.416580       NaN
22423450  5960  4950  7.278269  128.416580       NaN
22423451  5961  4950  7.275769  128.416580       NaN

[22423452 rows x 5 columns]

In [37]:
scaled0817_band = create_tif_band(scaled0817_df, "windvelo")
print(scaled0817_band.shape)

Start creating tif band at 09:57:33...
i: 0 at 09:57:33...
i: 10000 at 09:57:36...
i: 20000 at 09:57:38...
i: 30000 at 09:57:39...
i: 40000 at 09:57:41...
i: 50000 at 09:57:43...
i: 60000 at 09:57:45...
i: 70000 at 09:57:46...
i: 80000 at 09:57:48...
i: 90000 at 09:57:50...
i: 100000 at 09:57:51...
i: 110000 at 09:57:53...
i: 120000 at 09:57:55...
i: 130000 at 09:57:57...
i: 140000 at 09:57:58...
i: 150000 at 09:58:00...
i: 160000 at 09:58:02...
i: 170000 at 09:58:04...
i: 180000 at 09:58:05...
i: 190000 at 09:58:07...
i: 200000 at 09:58:09...
i: 210000 at 09:58:10...
i: 220000 at 09:58:12...
i: 230000 at 09:58:14...
i: 240000 at 09:58:16...
i: 250000 at 09:58:17...
i: 260000 at 09:58:19...
i: 270000 at 09:58:21...
i: 280000 at 09:58:22...
i: 290000 at 09:58:24...
i: 300000 at 09:58:26...
i: 310000 at 09:58:28...
i: 320000 at 09:58:29...
i: 330000 at 09:58:31...
i: 340000 at 09:58:33...
i: 350000 at 09:58:34...
i: 360000 at 09:58:36...
i: 370000 at 09:58:38...
i: 380000 at 09:58:40...


i: 3180000 at 10:06:41...
i: 3190000 at 10:06:43...
i: 3200000 at 10:06:45...
i: 3210000 at 10:06:46...
i: 3220000 at 10:06:48...
i: 3230000 at 10:06:50...
i: 3240000 at 10:06:52...
i: 3250000 at 10:06:53...
i: 3260000 at 10:06:55...
i: 3270000 at 10:06:57...
i: 3280000 at 10:06:58...
i: 3290000 at 10:07:00...
i: 3300000 at 10:07:02...
i: 3310000 at 10:07:03...
i: 3320000 at 10:07:05...
i: 3330000 at 10:07:07...
i: 3340000 at 10:07:09...
i: 3350000 at 10:07:10...
i: 3360000 at 10:07:12...
i: 3370000 at 10:07:14...
i: 3380000 at 10:07:16...
i: 3390000 at 10:07:17...
i: 3400000 at 10:07:19...
i: 3410000 at 10:07:21...
i: 3420000 at 10:07:23...
i: 3430000 at 10:07:24...
i: 3440000 at 10:07:26...
i: 3450000 at 10:07:28...
i: 3460000 at 10:07:29...
i: 3470000 at 10:07:31...
i: 3480000 at 10:07:33...
i: 3490000 at 10:07:35...
i: 3500000 at 10:07:36...
i: 3510000 at 10:07:38...
i: 3520000 at 10:07:40...
i: 3530000 at 10:07:41...
i: 3540000 at 10:07:43...
i: 3550000 at 10:07:45...
i: 3560000 a

i: 6340000 at 10:15:46...
i: 6350000 at 10:15:48...
i: 6360000 at 10:15:49...
i: 6370000 at 10:15:51...
i: 6380000 at 10:15:53...
i: 6390000 at 10:15:54...
i: 6400000 at 10:15:56...
i: 6410000 at 10:15:58...
i: 6420000 at 10:16:00...
i: 6430000 at 10:16:01...
i: 6440000 at 10:16:03...
i: 6450000 at 10:16:05...
i: 6460000 at 10:16:07...
i: 6470000 at 10:16:09...
i: 6480000 at 10:16:11...
i: 6490000 at 10:16:14...
i: 6500000 at 10:16:16...
i: 6510000 at 10:16:18...
i: 6520000 at 10:16:20...
i: 6530000 at 10:16:22...
i: 6540000 at 10:16:24...
i: 6550000 at 10:16:26...
i: 6560000 at 10:16:28...
i: 6570000 at 10:16:30...
i: 6580000 at 10:16:32...
i: 6590000 at 10:16:34...
i: 6600000 at 10:16:35...
i: 6610000 at 10:16:37...
i: 6620000 at 10:16:39...
i: 6630000 at 10:16:41...
i: 6640000 at 10:16:42...
i: 6650000 at 10:16:44...
i: 6660000 at 10:16:46...
i: 6670000 at 10:16:47...
i: 6680000 at 10:16:49...
i: 6690000 at 10:16:51...
i: 6700000 at 10:16:53...
i: 6710000 at 10:16:54...
i: 6720000 a

i: 9500000 at 10:24:57...
i: 9510000 at 10:24:58...
i: 9520000 at 10:25:00...
i: 9530000 at 10:25:02...
i: 9540000 at 10:25:04...
i: 9550000 at 10:25:05...
i: 9560000 at 10:25:07...
i: 9570000 at 10:25:09...
i: 9580000 at 10:25:11...
i: 9590000 at 10:25:13...
i: 9600000 at 10:25:14...
i: 9610000 at 10:25:16...
i: 9620000 at 10:25:18...
i: 9630000 at 10:25:20...
i: 9640000 at 10:25:21...
i: 9650000 at 10:25:23...
i: 9660000 at 10:25:25...
i: 9670000 at 10:25:26...
i: 9680000 at 10:25:28...
i: 9690000 at 10:25:30...
i: 9700000 at 10:25:32...
i: 9710000 at 10:25:33...
i: 9720000 at 10:25:35...
i: 9730000 at 10:25:37...
i: 9740000 at 10:25:38...
i: 9750000 at 10:25:40...
i: 9760000 at 10:25:42...
i: 9770000 at 10:25:44...
i: 9780000 at 10:25:45...
i: 9790000 at 10:25:47...
i: 9800000 at 10:25:49...
i: 9810000 at 10:25:51...
i: 9820000 at 10:25:52...
i: 9830000 at 10:25:54...
i: 9840000 at 10:25:56...
i: 9850000 at 10:25:57...
i: 9860000 at 10:25:59...
i: 9870000 at 10:26:01...
i: 9880000 a

i: 12560000 at 10:33:56...
i: 12570000 at 10:33:57...
i: 12580000 at 10:33:59...
i: 12590000 at 10:34:01...
i: 12600000 at 10:34:02...
i: 12610000 at 10:34:04...
i: 12620000 at 10:34:06...
i: 12630000 at 10:34:08...
i: 12640000 at 10:34:09...
i: 12650000 at 10:34:11...
i: 12660000 at 10:34:13...
i: 12670000 at 10:34:15...
i: 12680000 at 10:34:16...
i: 12690000 at 10:34:18...
i: 12700000 at 10:34:20...
i: 12710000 at 10:34:22...
i: 12720000 at 10:34:23...
i: 12730000 at 10:34:25...
i: 12740000 at 10:34:27...
i: 12750000 at 10:34:28...
i: 12760000 at 10:34:30...
i: 12770000 at 10:34:32...
i: 12780000 at 10:34:34...
i: 12790000 at 10:34:35...
i: 12800000 at 10:34:37...
i: 12810000 at 10:34:39...
i: 12820000 at 10:34:41...
i: 12830000 at 10:34:42...
i: 12840000 at 10:34:44...
i: 12850000 at 10:34:46...
i: 12860000 at 10:34:47...
i: 12870000 at 10:34:49...
i: 12880000 at 10:34:51...
i: 12890000 at 10:34:53...
i: 12900000 at 10:34:54...
i: 12910000 at 10:34:56...
i: 12920000 at 10:34:58...
i

i: 15600000 at 10:42:57...
i: 15610000 at 10:42:58...
i: 15620000 at 10:43:00...
i: 15630000 at 10:43:02...
i: 15640000 at 10:43:03...
i: 15650000 at 10:43:05...
i: 15660000 at 10:43:07...
i: 15670000 at 10:43:09...
i: 15680000 at 10:43:11...
i: 15690000 at 10:43:13...
i: 15700000 at 10:43:15...
i: 15710000 at 10:43:17...
i: 15720000 at 10:43:19...
i: 15730000 at 10:43:20...
i: 15740000 at 10:43:22...
i: 15750000 at 10:43:24...
i: 15760000 at 10:43:26...
i: 15770000 at 10:43:28...
i: 15780000 at 10:43:29...
i: 15790000 at 10:43:31...
i: 15800000 at 10:43:33...
i: 15810000 at 10:43:35...
i: 15820000 at 10:43:36...
i: 15830000 at 10:43:38...
i: 15840000 at 10:43:40...
i: 15850000 at 10:43:42...
i: 15860000 at 10:43:44...
i: 15870000 at 10:43:45...
i: 15880000 at 10:43:47...
i: 15890000 at 10:43:49...
i: 15900000 at 10:43:51...
i: 15910000 at 10:43:53...
i: 15920000 at 10:43:54...
i: 15930000 at 10:43:56...
i: 15940000 at 10:43:58...
i: 15950000 at 10:44:00...
i: 15960000 at 10:44:01...
i

i: 18640000 at 10:52:02...
i: 18650000 at 10:52:04...
i: 18660000 at 10:52:06...
i: 18670000 at 10:52:07...
i: 18680000 at 10:52:09...
i: 18690000 at 10:52:11...
i: 18700000 at 10:52:12...
i: 18710000 at 10:52:14...
i: 18720000 at 10:52:16...
i: 18730000 at 10:52:18...
i: 18740000 at 10:52:19...
i: 18750000 at 10:52:21...
i: 18760000 at 10:52:23...
i: 18770000 at 10:52:25...
i: 18780000 at 10:52:26...
i: 18790000 at 10:52:28...
i: 18800000 at 10:52:30...
i: 18810000 at 10:52:31...
i: 18820000 at 10:52:33...
i: 18830000 at 10:52:35...
i: 18840000 at 10:52:37...
i: 18850000 at 10:52:38...
i: 18860000 at 10:52:41...
i: 18870000 at 10:52:43...
i: 18880000 at 10:52:45...
i: 18890000 at 10:52:48...
i: 18900000 at 10:52:52...
i: 18910000 at 10:52:54...
i: 18920000 at 10:52:57...
i: 18930000 at 10:52:59...
i: 18940000 at 10:53:02...
i: 18950000 at 10:53:05...
i: 18960000 at 10:53:08...
i: 18970000 at 10:53:11...
i: 18980000 at 10:53:14...
i: 18990000 at 10:53:18...
i: 19000000 at 10:53:21...
i

i: 21680000 at 11:01:38...
i: 21690000 at 11:01:40...
i: 21700000 at 11:01:42...
i: 21710000 at 11:01:44...
i: 21720000 at 11:01:45...
i: 21730000 at 11:01:47...
i: 21740000 at 11:01:49...
i: 21750000 at 11:01:51...
i: 21760000 at 11:01:52...
i: 21770000 at 11:01:54...
i: 21780000 at 11:01:56...
i: 21790000 at 11:01:58...
i: 21800000 at 11:02:00...
i: 21810000 at 11:02:01...
i: 21820000 at 11:02:03...
i: 21830000 at 11:02:05...
i: 21840000 at 11:02:07...
i: 21850000 at 11:02:09...
i: 21860000 at 11:02:10...
i: 21870000 at 11:02:12...
i: 21880000 at 11:02:14...
i: 21890000 at 11:02:16...
i: 21900000 at 11:02:17...
i: 21910000 at 11:02:19...
i: 21920000 at 11:02:21...
i: 21930000 at 11:02:23...
i: 21940000 at 11:02:24...
i: 21950000 at 11:02:26...
i: 21960000 at 11:02:28...
i: 21970000 at 11:02:30...
i: 21980000 at 11:02:31...
i: 21990000 at 11:02:33...
i: 22000000 at 11:02:35...
i: 22010000 at 11:02:37...
i: 22020000 at 11:02:38...
i: 22030000 at 11:02:40...
i: 22040000 at 11:02:42...
i

In [38]:
create_tif_map(scaled2025_band, "2026", "prophet")

Start writing to tif image at 11:07:11...
Done writing to tif image at 11:07:14...


In [39]:
create_tif_map(scaled0817_band, "0817", "flat_wv")

Start writing to tif image at 11:08:08...
Done writing to tif image at 11:08:10...


In [40]:
create_tif_map(scaled2020_wv_band, "2020", "flat_wv")

Start writing to tif image at 11:09:03...
Done writing to tif image at 11:09:05...


In [41]:
create_tif_map(scaled2020_fb_band, "2020", "flat_fb")

Start writing to tif image at 11:09:46...
Done writing to tif image at 11:09:49...


In [42]:
create_tif_map(scaled2020_fbe_band, "2020", "flat_fb_e")

Start writing to tif image at 11:10:04...
Done writing to tif image at 11:10:06...


In [43]:
create_tif_map(scaled2020_th_band, "2020", "flat_th")

Start writing to tif image at 11:10:38...
Done writing to tif image at 11:10:40...


In [44]:
create_tif_map(scaled2020_the_band, "2020", "flat_th_e")

Start writing to tif image at 11:10:52...
Done writing to tif image at 11:10:54...
